# The Battle of Neighborhoods 

## Introduction:

The purpose of this project is to show retail businesses (in this instance coffie shop) how they can explore cities looking for the best places to open up new shops. It will help businesses to find best approximate locations by making smart and efficient decision on selecting great neighborhood out of numbers of other neighborhoods in Toranto city center and New York (Manhattan). There are a lot of retail businesses in such a big cities like New York or Toronto and evry competitive advantige will be a great asset to them. 

This project will include features such as venue location information and their ratings but exclude the pricings for rent and products becouse in this way it could be used for broader audience.

## Problem Which Tried to Solve:

We are opening new coffie shop, however there are a lot of coffie shops in these cities and we need to determin which places are more suitible to open up a coffie shop.

## Data:

For this project we will be using Wikipedia, Foursquare, csv files and data stored in IBM cloud. From IBM cloud we will take data about New York neighberhoods. From Wikipedia and CSV file we will take data for Toronto neighborhoods. Then from Forsquare we will take data about venues and customer reviews. 

Using Foursquare location data we will analyze New York and Toronto area and their venues. Then we willl cluster the data in the neighborhoods and look for the one neighborhood with the least coffie shops in them. Then we would look at the reviews and look for the cluster with the badest coffie shop reviews. In this way there would be less competition.

For more details please refer to the Methilogy section

## Methodology:

### Analytic Approach

There is a opportunity to open a coffie shop in New York (Manhattan) or Toronto (Center). However there are a lot of coffie shops in these cities and we need to determin which places are more suitible to open up a coffee shop. 

Using K-means clustering method clasify cluster areas of the city to see where are the most room for a new coffee shop. Then using Forsquare rating data find out which cluster does not have good caffee shops in them.

### Data Requirements

Using Foursquare location data we will analyze New York and Toronto area and their venues. Then we willl cluster the data in the neighborhoods and look for the one neighborhood with the least coffee shops in them. Then we would look at the reviews and look for the cluster with the badest coffie shop reviews. In this way there would be less competition.

### Data Collection

There should be two seperate tables with the primary data of two cities (with coordinates, neighborhoods and venues). Once the data is clean we should cluster it and find the best cluster for coffie shop.We would, also, need a ratings data from Foursquare app. We will join this data to a cluster data to see which cluster is the best for a new coffee shop

### Data Understanding and Preparation

Data will be collected from Wikipedia, Foursquare, csv files and IBM cloud. From IBM cloud we will take data about New York neighberhoods. From Wikipedia and CSV file we will take data for Toronto neighborhoods. Then from Forsquare we will take data about venues and customer reviews.

### Modeling and Evaluation

After clusters are created we will look for fewest coffie shops in the clusters and we would look for worst reviews for coffie shops in the cluster. Then we would know approximate position for our coffie shop and after that we will compare the best neighborhoods for each city.

Importing all necessary packages

In [2]:
import numpy as np # library to handle data in a vectorized manner
import scipy as sc

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

!pip install wget
import wget

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


Downloading the data from IBM cloud with neighborhood data.

In [3]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
                             
print('Data downloaded!')

Data downloaded!


Next, let's load the data.

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Let's take a quick look at the data.

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

Let's define a new variable that includes this data.

In [6]:
neighborhoods_data = newyork_data['features']

Let's start by creating an empty dataframe.

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Taking a look at the empty dataframe to confirm that the columns are as intended.

In [8]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

See how many boroughs and neighborhoods the dataset has.

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


Let's segment and cluster only the neighborhoods in Manhattan. Let's slice the original dataframe and create a new dataframe of the Manhattan data.

In [12]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent ny_explorer, as shown below. Let's get the geographical coordinates of Manhattan.

In [13]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


Let's visualizat Manhattan and the neighborhoods in it

In [14]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

Define Foursquare Credentials and Version

In [111]:
Cell removed for confidential data reasons

Getting the neighborhood's latitude and longitude values.

In [16]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

Let's extracts the category of the venue

In [ ]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

2. Explore Neighborhoods in Manhattan

Let's create a function that creates the GET request and collects relevant information and puts in dataframe. It repeats the same process to all the neighborhoods in Manhattan.

In [17]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['id'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue ID',
                  'Venue Category']
    
    return(nearby_venues)

Now, let's write the code to run the above function on each neighborhood and create a new dataframe called manhattan_venues.

In [18]:
# type your answer here

manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude'],
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


Let's check the size of the resulting dataframe

In [19]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3007, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066    Bikram Yoga   
1  Marble Hill              40.876551               -73.91066       Arturo's   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066       Rite Aid   
4  Marble Hill              40.876551               -73.91066         Subway   

   Venue Latitude  Venue Longitude                  Venue ID  Venue Category  
0       40.876844       -73.906204  4baf59e8f964a520a6f93be3     Yoga Studio  
1       40.874412       -73.910271  4b4429abf964a52037f225e3     Pizza Place  
2       40.880404       -73.908937  4b79cc46f964a520c5122fe3           Diner  
3       40.875467       -73.908906  4b88e053f964a5208a1132e3        Pharmacy  
4       40.874667       -73.909586  4b4f7b65f964a5205a0827e3  Sandwich Place

Now, we will find all coffie shops in the list and assing it to a new dataframe.

In [20]:
manhatan_rating = manhattan_venues[['Venue ID', 'Venue Category']]
manhatan_rating

Venue ID                            Venue Category
0     4baf59e8f964a520a6f93be3                               Yoga Studio
1     4b4429abf964a52037f225e3                               Pizza Place
2     4b79cc46f964a520c5122fe3                                     Diner
3     4b88e053f964a5208a1132e3                                  Pharmacy
4     4b4f7b65f964a5205a0827e3                            Sandwich Place
5     5631194e498e2de074de661c                           Supplement Shop
6     4e4e4517bd4101d0d7a67568                            Ice Cream Shop
7     55f81cd2498ee903149fcc64                               Coffee Shop
8     4c852173dc018cfa2bc3e56c                                Kids Store
9     5af7b896012358002c42bf4a                              Optical Shop
10    4a725fa1f964a520f6da1fe3                            Tennis Stadium
11    5802a20c38fa8638a305e241                                    Bakery
12    4b9c9c43f964a520ac7236e3                            Discount Store
13    4e9356b4754a50cc7dc4d209                          Storage Facility
14    4e4ce4debd413c4cc66d05d0                            Sandwich Place
15    4b9c9c6af964a520b27236e3                        Seafood Restaurant
16    4ec68016cc21b428e1d2060a                                      Bank
17    546d31ca498e561c698a0320                          Department Store
18    4b5357adf964a520319827e3                                Donut Shop
19    55f751ca498eacc0307d1cfe                                       Gym
20    58f4fc2b829b0c305839877b                            Clothing Store
21    4dfe40df8877333e195b68fc                                Steakhouse
22    563b6b8c498eaf512bbd611e                        Miscellaneous Shop
23    4ed7956b8b81b2bf28adc714                             Deli / Bodega
24    5012c967e889cf0567e9e2d4                       American Restaurant
25    4b1896caf964a52069d423e3                            Sandwich Place
26    578692f4498e1054905dbde7                                     Hotel
27    5cd1aa6a9d746800394f556d                                    Bakery
28    5521c2ff498ebe2368634187                          Greek Restaurant
29    56c3c626cd106998d2b196d0                               Pizza Place
30    503fffabe4b05e5c0eace385                              Cocktail Bar
31    59318ce1c5b11c6c16c15d29                            Sandwich Place
32    4b37a3c9f964a5207e4325e3                                    Museum
33    4db3374590a0843f295fb69b                        Chinese Restaurant
34    5894c9a15e56b417cf79e553                        Chinese Restaurant
35    58f25962c5b11c7b5a2192de                            Ice Cream Shop
36    5596ea13498e6d86ec66d614                              Dessert Shop
37    56bf8899cd102af95de0a66e                       Indie Movie Theater
38    4b89ac72f964a520e94a32e3                          Asian Restaurant
39    557c335b498ec492c5d567dd                                 Bike Shop
40    4afde8eaf964a520f52b22e3                                       Spa
41    5f53b39cf2961d1a5638ae6f                                    Bakery
42    5d992946dbf3ca0008d05211                         Hotpot Restaurant
43    4edbbcf729c2b9122a06991c                                       Spa
44    4fd38a04e4b065401a9aaf88                   New American Restaurant
45    49e8ee2ef964a520af651fe3                              Noodle House
46    59480a78f62e090a3b4d6eb7                        Spanish Restaurant
47    535f8dc4498eab7f9ee19f7f                    Furniture / Home Store
48    576b3252498e33072627efba                           Bubble Tea Shop
49    522dfe8b7e4826517408a264                       American Restaurant
50    4a023f1df964a52040711fe3                                  Tea Room
51    5c65df02178a2a002c123450                               Karaoke Bar
52    5cc4e9d0c876c8002c3010cb                           Thai Restaurant
53    4b2ebc57f964a520e3e524e3                           Bubble Tea Shop
54    4

In [21]:
manhatan_rating2 = manhatan_rating[manhatan_rating['Venue Category'] == 'Coffee Shop'].reset_index(drop=True)
manhatan_rating2

Venue ID Venue Category
0    55f81cd2498ee903149fcc64    Coffee Shop
1    579f74eb498e9a4d6caabeda    Coffee Shop
2    5bafd8419de23b002c772a72    Coffee Shop
3    4aafdf93f964a520f66420e3    Coffee Shop
4    5c092ec2d1a402002cd083cb    Coffee Shop
5    55aa54bc498eac980f832bc9    Coffee Shop
6    4fef2f45e4b0562c835d6b7c    Coffee Shop
7    5b0345aa9ba3e5002c6bfeb8    Coffee Shop
8    58232a8d8b624d27650026e8    Coffee Shop
9    4ef4c5b099111bd0a9b8e9c2    Coffee Shop
10   59b6f86861f0700444627663    Coffee Shop
11   5b0edcd498fbfc002cfcad0e    Coffee Shop
12   58b2f2f60037eb7f1a778535    Coffee Shop
13   5145d153e4b0887518ec0317    Coffee Shop
14   4b69efa9f964a52014bd2be3    Coffee Shop
15   4a819c70f964a52006f71fe3    Coffee Shop
16   4e9078d6b63456ab9570ec12    Coffee Shop
17   59ff7d490a464d2738a23962    Coffee Shop
18   4ef4c5b099111bd0a9b8e9c2    Coffee Shop
19   599f1eb6fd16bb4a5da9d3f9    Coffee Shop
20   4b0807abf964a520890223e3    Coffee Shop
21   4a773e0df964a520f1e31fe3    Coffee Shop
22   589634906c682b1f845ae6dc    Coffee Shop
23   4fc64ab9e4b0acb95c508a5f    Coffee Shop
24   544e883b498e01e80f241740    Coffee Shop
25   560e84e2498ee6bcb7ea28be    Coffee Shop
26   5c683caaf96b2c00397a8609    Coffee Shop
27   5a8ce147bed4832067bea15e    Coffee Shop
28   53bad291498e3c01b5629fe8    Coffee Shop
29   5dd83fae6690dd00088cb92f    Coffee Shop
30   53a46354498e7d482877cf67    Coffee Shop
31   526d9114498ec8efda93fcce    Coffee Shop
32   54566365498e4fb5ed4fe987    Coffee Shop
33   5491e424498e93529c115699    Coffee Shop
34   57f27362498ef61538900f04    Coffee Shop
35   516bf3c5e4b0e8d4443da599    Coffee Shop
36   4caf199db4b0a35dc8033ece    Coffee Shop
37   59c5401847f8762d3d4e023a    Coffee Shop
38   572759e0498efe726c551007    Coffee Shop
39   536fe442498e193806dedd8f    Coffee Shop
40   519a94e3498e722d3d9ae1bf    Coffee Shop
41   5c13bf838afbe0002de55061    Coffee Shop
42   569aa89d498e5a25c05fdfec    Coffee Shop
43   4f3a9e05bb3d2fbe725ca57a    Coffee Shop
44   55e9f118498eda28f897f9e3    Coffee Shop
45   573498df498e6df2eb8b36a7    Coffee Shop
46   5f3ecdaa960de027c22a9e80    Coffee Shop
47   3fd66200f964a52059e61ee3    Coffee Shop
48   49d36ca4f964a520f75b1fe3    Coffee Shop
49   5bb4cdac28374e002bac356a    Coffee Shop
50   47fdf872f964a520e14e1fe3    Coffee Shop
51   4f6a28d5e4b085e9a4b3c5e1    Coffee Shop
52   4ea0afbf9adf1e334e4cc0e6    Coffee Shop
53   4a118d01f964a52023771fe3    Coffee Shop
54   57bf76a2498e98061d338fe3    Coffee Shop
55   5d920337a6193400088e446d    Coffee Shop
56   5f3ecdaa960de027c22a9e80    Coffee Shop
57   573498df498e6df2eb8b36a7    Coffee Shop
58   49d2b43ef964a520cb5b1fe3    Coffee Shop
59   5b8c24546dcf04002c9c673c    Coffee Shop
60   5418490f498e4d3bb75c7bcc    Coffee Shop
61   546cb126498eabb0f206d61f    Coffee Shop
62   5d864371ebc5f80008c24794    Coffee Shop
63   54733f59498e78d5fb3a0755    Coffee Shop
64   5f9d9d9010b05638bb879711    Coffee Shop
65   40f32600f964a520720a1fe3    Coffee Shop
66   5b44c582d8096e002ccd329a    Coffee Shop
67   580226bb38fae0dde3f6bd9a    Coffee Shop
68   4a704000f964a52040d71fe3    Coffee Shop
69   4ce41f161594236ac316fb49    Coffee Shop
70   5dba113267232c000803cb37    Coffee Shop
71   59bd506ce2d4aa3d68b99a88    Coffee Shop
72   574456e5498e39c73d234da1    Coffee Shop
73   5ef8e6aef272db0008a81a76    Coffee Shop
74   5cf965947564f7002c79aa21    Coffee Shop
75   500d3cede4b0f6804faa90a8    Coffee Shop
76   5f11ef5e938b7c3b5ead3c4f    Coffee Shop
77   561a8cd8498ed81f4384d0aa    Coffee Shop
78   5dfa92d864192300086a1931    Coffee Shop
79   566de7e3498e30e4798117ae    Coffee Shop
80   59bd506ce2d4aa3d68b99a88    Coffee Shop
81   599d7c7e61f0700d414c282b    Coffee Shop
82   5abb96b31f8ed641d150eafa    Coffee Shop
83   51ae935b7dd2de27a217609e    Coffee Shop
84   57fd457a498e39cd34012586    Coffee Shop
85   552a7fbb498e1e8662ac8146    Coffee Shop
86   56c73a4a498ea736d7388245    Coffee Shop
87   5682a50a498e25a5a1d870a2    Coffee Shop
88   4f22b060e4b

We will have to slice dataframe into 3 dataframes run the code to get ratings for each coffe shop and then merge it back together due to Foursquare limitations.

Lets name our data slices nearby_venues_part1, nearby_venues_part2 and nearby_venues_part3

In [23]:
venues_list2=[]
for venueid in manhatan_rating2['Venue ID'][14:15]:
    print(venueid)
    url1 = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
            venueid,
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION 
            )
            
    result = requests.get(url1).json()['response']       
    
    for v in result:
        try:
            venues_list2.append([
                venueid,
                result['venue']['rating']])
            
        except:
            venues_list2.append([
                venueid,
                'NaN'])
                    
nearby_venues2 = pd.DataFrame(venues_list2, columns=['Venue ID','Ratings'])

4b69efa9f964a52014bd2be3


Let's see if datfarem is filled

In [24]:
nearby_venues2.shape

(1, 2)

In [25]:
nearby_venues2

Venue ID  Ratings
0  4b69efa9f964a52014bd2be3      6.9

In [28]:
# nearby_venues_part1 = nearby_venues2
#nearby_venues_part1

In [29]:
# nearby_venues_part2 = nearby_venues2
#nearby_venues_part2

In [30]:
# nearby_venues_part3 = nearby_venues2
#nearby_venues_part3

Now, let's merge them back together and drop venue which did not have a rating.

In [31]:
#frames = [nearby_venues_part1, nearby_venues_part2, nearby_venues_part3]

#nearby_venues_ratings = pd.concat(frames).reset_index(drop=True)

#nearby_venues_ratings = nearby_venues_ratings.drop(nearby_venues_ratings.index[9]).reset_index(drop=True)

Since it took me longer to extract this data I stored it in excel sheet incase of a crash and it was worth it.

I will import data which was gathered with code in coments above from my computer and drop 7th row since it has no rating in it.

In [68]:
nearby_venues_ratings=pd.read_csv(r'C:\Users\Ramiu\Desktop\ibm\capstone\ratingsi.csv')
nearby_venues_ratings = nearby_venues_ratings.drop(nearby_venues_ratings.index[7]).reset_index(drop=True)

In [69]:
nearby_venues_ratings

Venue ID  Rating
0    55f81cd2498ee903149fcc64     7.7
1    579f74eb498e9a4d6caabeda     8.8
2    5bafd8419de23b002c772a72     8.0
3    4aafdf93f964a520f66420e3     6.4
4    5c092ec2d1a402002cd083cb     8.2
5    55aa54bc498eac980f832bc9     8.0
6    4fef2f45e4b0562c835d6b7c     7.2
7    58232a8d8b624d27650026e8     7.9
8    4ef4c5b099111bd0a9b8e9c2     7.7
9    59b6f86861f0700444627663     7.5
10   5b0edcd498fbfc002cfcad0e     9.0
11   58b2f2f60037eb7f1a778535     7.4
12   5145d153e4b0887518ec0317     7.0
13   4b69efa9f964a52014bd2be3     6.9
14   4a819c70f964a52006f71fe3     6.4
15   4e9078d6b63456ab9570ec12     8.6
16   59ff7d490a464d2738a23962     7.7
17   599f1eb6fd16bb4a5da9d3f9     7.1
18   4b0807abf964a520890223e3     6.0
19   4a773e0df964a520f1e31fe3     8.1
20   589634906c682b1f845ae6dc     7.9
21   4fc64ab9e4b0acb95c508a5f     7.9
22   544e883b498e01e80f241740     7.5
23   560e84e2498ee6bcb7ea28be     7.1
24   5c683caaf96b2c00397a8609     8.4
25   5a8ce147bed4832067bea15e     9.0
26   53bad291498e3c01b5629fe8     8.1
27   5dd83fae6690dd00088cb92f     7.2
28   53a46354498e7d482877cf67     7.4
29   526d9114498ec8efda93fcce     6.9
30   54566365498e4fb5ed4fe987     8.6
31   5491e424498e93529c115699     7.8
32   57f27362498ef61538900f04     8.7
33   516bf3c5e4b0e8d4443da599     8.0
34   4caf199db4b0a35dc8033ece     7.8
35   59c5401847f8762d3d4e023a     8.1
36   572759e0498efe726c551007     7.9
37   536fe442498e193806dedd8f     7.4
38   519a94e3498e722d3d9ae1bf     9.0
39   5c13bf838afbe0002de55061     8.4
40   569aa89d498e5a25c05fdfec     8.0
41   4f3a9e05bb3d2fbe725ca57a     8.2
42   55e9f118498eda28f897f9e3     8.4
43   573498df498e6df2eb8b36a7     8.9
44   5f3ecdaa960de027c22a9e80     9.2
45   3fd66200f964a52059e61ee3     8.6
46   49d36ca4f964a520f75b1fe3     8.5
47   5bb4cdac28374e002bac356a     8.5
48   47fdf872f964a520e14e1fe3     8.4
49   4f6a28d5e4b085e9a4b3c5e1     7.5
50   4ea0afbf9adf1e334e4cc0e6     8.5
51   4a118d01f964a52023771fe3     8.5
52   57bf76a2498e98061d338fe3     8.2
53   5d920337a6193400088e446d     8.7
54   49d2b43ef964a520cb5b1fe3     8.4
55   5b8c24546dcf04002c9c673c     8.9
56   5418490f498e4d3bb75c7bcc     8.5
57   546cb126498eabb0f206d61f     8.6
58   5d864371ebc5f80008c24794     8.0
59   54733f59498e78d5fb3a0755     7.7
60   5f9d9d9010b05638bb879711     8.4
61   40f32600f964a520720a1fe3     8.0
62   5b44c582d8096e002ccd329a     8.5
63   580226bb38fae0dde3f6bd9a     7.5
64   4a704000f964a52040d71fe3     5.8
65   4ce41f161594236ac316fb49     7.7
66   5dba113267232c000803cb37     7.4
67   59bd506ce2d4aa3d68b99a88     8.4
68   574456e5498e39c73d234da1     9.0
69   5ef8e6aef272db0008a81a76     8.4
70   5cf965947564f7002c79aa21     9.0
71   500d3cede4b0f6804faa90a8     8.3
72   5f11ef5e938b7c3b5ead3c4f     8.9
73   561a8cd8498ed81f4384d0aa     8.0
74   5dfa92d864192300086a1931     8.7
75   566de7e3498e30e4798117ae     8.3
76   599d7c7e61f0700d414c282b     8.2
77   5abb96b31f8ed641d150eafa     8.6
78   51ae935b7dd2de27a217609e     7.8
79   57fd457a498e39cd34012586     7.4
80   552a7fbb498e1e8662ac8146     7.5
81   56c73a4a498ea736d7388245     8.6
82   5682a50a498e25a5a1d870a2     8.5
83   4f22b060e4b02a95fc886761     8.3
84   5c7d2d843d4791002c881f1c     7.7
85   597a11ccb2958f056b27c60d     8.0
86   571b7b0b38faaa76e596e8a1     7.5
87   56e7f585498ed6598b4030cd     7.5
88   5a09b45b6dcf043c23d5ad4e     8.6
89   59ac2ec6fdb9a734dd847025     8.7
90   4aa52d50f964a520834720e3     8.7
91   5942ed444c9be62191dbaf80     7.4
92   53ce4d05498e4047bd6e9519     8.7
93   55ca5d85498e594f7095854a     7.8
94   51b70eb9454a121ab89e5c42     7.0
95   507db18ae4b0f570fa6bf5bc     6.1
96   5d7bb678290f5e00075785d9     7.3
97   457bd9adf964a520f63e1fe3     7.5
98   5890d8aecc5b6a43d6daa0f9     8.2
99   5b9d8e69b6eedb002c72a39e     8.2
100  5d2763ff8c3f0400235dbd57     8.4

Let's check how many venues were returned for each neighborhood

In [35]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       61                      61     61   
Carnegie Hill                           73                      73     73   
Central Harlem                          40                      40     40   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                            84                      84     84   
Clinton                                100                     100    100   
East Harlem                             41                      41     41   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                61                      61     61   
Greenwich Village                      100                     100    100   
Hamilton Heights                        54                      54     54   
Hudson Yards                            60                      60     60   
Inwood                                  55                      55     55   
Lenox Hill                             100                     100    100   
Lincoln Square                          95                      95     95   
Little Italy                           100                     100    100   
Lower East Side                         35                      35     35   
Manhattan Valley                        39                      39     39   
Manhattanville                          38                      38     38   
Marble Hill                             25                      25     25   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     40                      40     40   
Murray Hill                             99                      99     99   
Noho                                   100                     100    100   
Roosevelt Island                        31                      31     31   
Soho                                   100                     100    100   
Stuyvesant Town                         17                      17     17   
Sutton Place                            91                      91     91   
Tribeca                                 77                      77     77   
Tudor City                              74                      74     74   
Turtle Bay                              93                      93     93   
Upper East Side                         78                      78     78   
Upper West Side                         71                      71     71   
Washington Heights                      81                      81     81   
West Village                           100                     100    100   
Yorkville                               94                      94     94   

                     Venue Latitude  Venue Longitude  Venue ID  Venue Category  
Neighborhood                                                                    
Battery Park City                61               61        61              61  
Carnegie Hill                    73               73        73              73  
Central Harlem                   40               40        40              40  
Chelsea                         100              100       100             100  
Chinatown                       100              100       100             100  
Civic Center                     84               84        84              84  
Clinton                         100              100       100             100  
East Harlem                      41               41     

Let's find out how many unique categories can be curated from all the returned venues

In [36]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 330 uniques categories.


#### Analyzing Each Neighborhood for Manhattan

In [37]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  \
0                   0                    0             0   
1                   0                    0             0   
2                   0                    0             0   
3                   0                    0             0   
4                   0                    0             0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                    0              0          0           0           0   
1                    0              0          0           0           0   
2                    0              0          0           0           0   
3                    0              0          0           0           0   
4                    0              0          0           0           0   

   Bakery  Bank  Bar  Basketball Court  Beer Bar  Beer Garden  Beer Store  \
0       0     0    0                 0         0            0           0   
1       0     0    0                 0         0            0           0   
2       0     0    0                 0         0            0           0   
3       0     0    0                 0         0            0           0   
4       0     0    0                 0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0           0              0          0         0           0   
1           0              0          0         0           0   
2           0              0          0         0           0   
3           0              0          0         0           0   
4           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  \
0                     0               0        0       0                0   
1                     0               0        0       0                0   
2                     0               0        0       0                0   
3                     0               0        0       0                0   
4                     0               0        0       0                0   

   Building  Burger Joint  Burrito Place  Bus Line 

And let's examine the new dataframe size.


In [38]:
manhattan_onehot.shape

(3007, 331)

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [39]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000        0.000000               0.00   
1         Carnegie Hill           0.000000        0.000000               0.00   
2        Central Harlem           0.000000        0.000000               0.00   
3               Chelsea           0.000000        0.000000               0.00   
4             Chinatown           0.000000        0.000000               0.00   
5          Civic Center           0.000000        0.000000               0.00   
6               Clinton           0.000000        0.000000               0.00   
7           East Harlem           0.000000        0.000000               0.00   
8          East Village           0.000000        0.000000               0.00   
9    Financial District           0.010000        0.000000               0.00   
10             Flatiron           0.000000        0.000000               0.00   
11             Gramercy           0.000000        0.000000               0.00   
12    Greenwich Village           0.020000        0.000000               0.00   
13     Hamilton Heights           0.000000        0.018519               0.00   
14         Hudson Yards           0.000000        0.000000               0.00   
15               Inwood           0.000000        0.000000               0.00   
16           Lenox Hill           0.000000        0.000000               0.01   
17       Lincoln Square           0.010526        0.000000               0.00   
18         Little Italy           0.000000        0.000000               0.00   
19      Lower East Side           0.000000        0.000000               0.00   
20     Manhattan Valley           0.000000        0.000000               0.00   
21       Manhattanville           0.000000        0.000000               0.00   
22          Marble Hill           0.000000        0.000000               0.00   
23              Midtown           0.000000        0.000000               0.00   
24        Midtown South           0.000000        0.000000               0.00   
25  Morningside Heights           0.000000        0.000000               0.00   
26          Murray Hill           0.000000        0.000000               0.00   
27                 Noho           0.000000        0.000000               0.00   
28     Roosevelt Island           0.000000        0.000000               0.00   
29                 Soho           0.000000        0.000000               0.00   
30      Stuyvesant Town           0.000000        0.000000               0.00   
31         Sutton Place           0.000000        0.010989               0.00   
32              Tribeca           0.000000        0.000000               0.00   
33           Tudor City           0.000000        0.000000               0.00   
34           Turtle Bay           0.000000        0.000000               0.00   
35      Upper East Side           0.000000        0.000000               0.00   
36      Upper West Side           0.000000        0.000000               0.00   
37   Washington Heights           0.000000        0.000000               0.00   
38         West Village           0.010000        0.010000               0.00   
39            Yorkville           0.000000        0.000000               0.00   

    African Restaurant  American Restaurant  Antique Shop  \
0                0.000             0.000000      0.000000   
1                0.000             0.013699      0.000000   
2                0.075             0.050000      0.000000   
3                0.000             0.030000      0.000000   
4                0.000             0.030000      0.000000   
5                0.000             0.011905      0.011905   
6                0.000             0.050000      0.000000   
7                0.000             0.000000      0.000000   
8                0.000             0.010000      0.000000   
9                0.000             0.030000      0.000000   
10               0

Let's confirm the new size

In [40]:
manhattan_grouped.shape

(40, 331)

Let's put that into a pandas dataframe

First, let's write a function to sort the venues in descending order.


In [41]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [42]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Coffee Shop             Wine Shop   
2     Central Harlem    African Restaurant  Gym / Fitness Center   
3            Chelsea           Art Gallery           Coffee Shop   
4          Chinatown                Bakery    Chinese Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop                   Gym         Memorial Site   
1           Pizza Place        Cosmetics Shop                   Gym   
2   American Restaurant        Sandwich Place    Seafood Restaurant   
3                Bakery             Wine Shop   American Restaurant   
4          Cocktail Bar          Noodle House    Salon / Barbershop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Shopping Mall          Gourmet Shop    Chinese Restaurant   
1                  Café           Yoga Studio            Art Museum   
2                   Bar     French Restaurant                  Café   
3        Ice Cream Shop     French Restaurant          Cycle Studio   
4        Ice Cream Shop   American Restaurant          Dessert Shop   

  9th Most Common Venue 10th Most Common Venue  
0            Food Court                  Plaza  
1   Japanese Restaurant   Gym / Fitness Center  
2         Grocery Store                    Gym  
3          Cupcake Shop                Theater  
4                   Spa           Optical Shop

4. Cluster Neighborhoods

Run k-means to cluster the neighborhood into 5 clusters.

In [43]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 1, 0, 0, 0, 0, 0, 4, 0, 1])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [44]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               0   
1  Manhattan           Chinatown  40.715618 -73.994279               0   
2  Manhattan  Washington Heights  40.851903 -73.936900               4   
3  Manhattan              Inwood  40.867684 -73.921210               4   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place           Yoga Studio                 Diner   
1                Bakery    Chinese Restaurant          Cocktail Bar   
2                  Café         Grocery Store           Pizza Place   
3    Mexican Restaurant                Lounge                  Café   
4           Pizza Place    Mexican Restaurant                  Café   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0       Supplement Shop      Storage Facility            Steakhouse   
1          Noodle House    Salon / Barbershop        Ice Cream Shop   
2    Chinese Restaurant     Mobile Phone Shop                  Bank   
3                  Park                Bakery                  Bank   
4        Sandwich Place           Yoga Studio          Cocktail Bar   

  7th Most Common Venue 8th Most Common Venue      9th Most Common Venue  \
0        Clothing Store           Coffee Shop         Seafood Restaurant   
1   American Restaurant          Dessert Shop                        Spa   
2                Bakery              Pharmacy         Spanish Restaurant   
3         Deli / Bodega  Caribbean Restaurant                   Wine Bar   
4                Bakery     Mobile Phone Shop  Latin American Restaurant   

  10th Most Common Venue  
0       Department Store  
1           Optical Shop  
2       Tapas Restaurant  
3            Pizza Place  
4   Caribbean Restaurant

Finally, let's visualize the resulting clusters

In [45]:
manhattan_merged

Borough         Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Manhattan          Marble Hill  40.876551 -73.910660               0   
1   Manhattan            Chinatown  40.715618 -73.994279               0   
2   Manhattan   Washington Heights  40.851903 -73.936900               4   
3   Manhattan               Inwood  40.867684 -73.921210               4   
4   Manhattan     Hamilton Heights  40.823604 -73.949688               4   
5   Manhattan       Manhattanville  40.816934 -73.957385               0   
6   Manhattan       Central Harlem  40.815976 -73.943211               0   
7   Manhattan          East Harlem  40.792249 -73.944182               4   
8   Manhattan      Upper East Side  40.775639 -73.960508               1   
9   Manhattan            Yorkville  40.775930 -73.947118               1   
10  Manhattan           Lenox Hill  40.768113 -73.958860               1   
11  Manhattan     Roosevelt Island  40.762160 -73.949168               2   
12  Manhattan      Upper West Side  40.787658 -73.977059               1   
13  Manhattan       Lincoln Square  40.773529 -73.985338               0   
14  Manhattan              Clinton  40.759101 -73.996119               0   
15  Manhattan              Midtown  40.754691 -73.981669               0   
16  Manhattan          Murray Hill  40.748303 -73.978332               0   
17  Manhattan              Chelsea  40.744035 -74.003116               0   
18  Manhattan    Greenwich Village  40.726933 -73.999914               1   
19  Manhattan         East Village  40.727847 -73.982226               0   
20  Manhattan      Lower East Side  40.717807 -73.980890               4   
21  Manhattan              Tribeca  40.721522 -74.010683               0   
22  Manhattan         Little Italy  40.719324 -73.997305               1   
23  Manhattan                 Soho  40.722184 -74.000657               1   
24  Manhattan         West Village  40.734434 -74.006180               1   
25  Manhattan     Manhattan Valley  40.797307 -73.964286               4   
26  Manhattan  Morningside Heights  40.808000 -73.963896               0   
27  Manhattan             Gramercy  40.737210 -73.981376               1   
28  Manhattan    Battery Park City  40.711932 -74.016869               0   
29  Manhattan   Financial District  40.707107 -74.010665               1   
30  Manhattan        Carnegie Hill  40.782683 -73.953256               1   
31  Manhattan                 Noho  40.723259 -73.988434               1   
32  Manhattan         Civic Center  40.715229 -74.005415               0   
33  Manhattan        Midtown South  40.748510 -73.988713               0   
34  Manhattan         Sutton Place  40.760280 -73.963556               0   
35  Manhattan           Turtle Bay  40.752042 -73.967708               0   
36  Manhattan           Tudor City  40.746917 -73.971219               0   
37  Manhattan      Stuyvesant Town  40.731000 -73.974052               3   
38  Manhattan             Flatiron  40.739673 -73.990947               1   
39  Manhattan         Hudson Yards  40.756658 -74.000111               0   

   1st Most Common Venue 2nd Most Common Venue          3rd Most Common Venue  \
0         Sandwich Place           Yoga Studio                          Diner   
1                 Bakery    Chinese Restaurant                   Cocktail Bar   
2                   Café         Grocery Store                    Pizza Place   
3     Mexican Restaurant                Lounge                           Café   
4            Pizza Place    Mexican Restaurant                           Café   
5            Coffee Shop    Italian Restaurant                           Bank   
6     African Restaurant  Gym / Fitness Center            American Restaurant   
7            Pizza Place                Bakery             Mexican Restaurant   
8     Italian Restaurant               Exhibit                         Bakery   
9     Italian Restaurant      Sushi Restaurant                    Coffee Shop  

In [46]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

5. Examine Clusters

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

Manhattan Cluster 1

In [47]:
Cluster1 = manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]
Cluster1

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0           Marble Hill        Sandwich Place           Yoga Studio   
1             Chinatown                Bakery    Chinese Restaurant   
5        Manhattanville           Coffee Shop    Italian Restaurant   
6        Central Harlem    African Restaurant  Gym / Fitness Center   
13       Lincoln Square          Concert Hall                  Café   
14              Clinton           Coffee Shop    Italian Restaurant   
15              Midtown                 Hotel        Clothing Store   
16          Murray Hill           Coffee Shop   American Restaurant   
17              Chelsea           Art Gallery           Coffee Shop   
19         East Village                   Bar              Wine Bar   
21              Tribeca                   Spa                  Park   
26  Morningside Heights             Bookstore                  Café   
28    Battery Park City                  Park                 Hotel   
32         Civic Center           Coffee Shop                   Spa   
33        Midtown South     Korean Restaurant                 Hotel   
34         Sutton Place    Italian Restaurant                  Park   
35           Turtle Bay    Italian Restaurant                  Park   
36           Tudor City                  Park                  Café   
39         Hudson Yards   American Restaurant  Gym / Fitness Center   

            3rd Most Common Venue 4th Most Common Venue  \
0                           Diner       Supplement Shop   
1                    Cocktail Bar          Noodle House   
5                            Bank            Food Truck   
6             American Restaurant        Sandwich Place   
13                          Plaza               Theater   
14                        Theater        Sandwich Place   
15                        Theater                   Spa   
16                          Hotel  Gym / Fitness Center   
17                         Bakery             Wine Shop   
19  Vegetarian / Vegan Restaurant           Coffee Shop   
21             Italian Restaurant                  Café   
26                  Deli / Bodega              Pharmacy   
28                    Coffee Shop                   Gym   
32           Gym / Fitness Center     French Restaurant   
33                      Hotel Bar                Bakery   
34                          Hotel                   Spa   
35                     Steakhouse         Deli / Bodega   
36                           Bank         Deli / Bodega   
39             Italian Restaurant            Restaurant   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Storage Facility            Steakhouse        Clothing Store   
1      Salon / Barbershop        Ice Cream Shop   American Restaurant   
5      Mexican Restaurant      Sushi Restaurant           Supermarket   
6      Seafood Restaurant                   Bar     French Restaurant   
13  Performing Arts Venue  Gym / Fitness Center                Bakery   
14    American Restaurant                   Gym  Gym / Fitness Center   
15            Coffee Shop            Food Truck      Sushi Restaurant   
16    Japanese Restaurant                   Spa        Sandwich Place   
17    American Restaurant        Ice Cream Shop     French Restaurant   
19      Korean Restaurant    Mexican Restaurant        Ice Cream Shop   
21       Greek Restaurant            Skate Park        Scenic Lookout   
26                   Park        Sandwich Place           Coffee Shop   
28          Memorial Site         Shopping Mall          Gourmet Shop   
32           Cocktail Bar                 Hotel           Yoga Studio   
33   Gym / Fitness Center                  Café           Coffee Shop   
34             Steakhouse                   Gym           Pizza Place   
35     Seafood Restaurant           Coffee Shop      Sushi Restaurant   
36     Mexican Restaurant        Ice Cream Shop      Sushi Restaurant   
39           Burger Jo

Now, we will extract the Neighbrhoods from Cluster1 dataframe and find all Coffie shops in these Neighborhoods

In [48]:
Cluster1_Neighborhood = Cluster1['Neighborhood'].reset_index(drop=True)
Cluster1_Neighborhood

0             Marble Hill
1               Chinatown
2          Manhattanville
3          Central Harlem
4          Lincoln Square
5                 Clinton
6                 Midtown
7             Murray Hill
8                 Chelsea
9            East Village
10                Tribeca
11    Morningside Heights
12      Battery Park City
13           Civic Center
14          Midtown South
15           Sutton Place
16             Turtle Bay
17             Tudor City
18           Hudson Yards
Name: Neighborhood, dtype: object

In [61]:
manhattan_venues_coffee = manhattan_venues[(manhattan_venues['Neighborhood'].str.contains("Marble Hill|Chinatown|Manhattanville|Central Harlem|Lincoln Square|Clinton|Midtown|Murray Hill|Chelsea|East Village|Tribeca|Morningside Heights|Battery Park City|Civic Center|Midtown South|Sutton Place|Turtle Bay|Tudor City|Hudson Yards")) & (manhattan_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
manhattan_venues_coffee

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Marble Hill              40.876551              -73.910660   
1             Chinatown              40.715618              -73.994279   
2        Manhattanville              40.816934              -73.957385   
3        Manhattanville              40.816934              -73.957385   
4        Lincoln Square              40.773529              -73.985338   
5        Lincoln Square              40.773529              -73.985338   
6               Clinton              40.759101              -73.996119   
7               Clinton              40.759101              -73.996119   
8               Clinton              40.759101              -73.996119   
9               Clinton              40.759101              -73.996119   
10              Clinton              40.759101              -73.996119   
11              Clinton              40.759101              -73.996119   
12              Midtown              40.754691              -73.981669   
13              Midtown              40.754691              -73.981669   
14              Midtown              40.754691              -73.981669   
15          Murray Hill              40.748303              -73.978332   
16          Murray Hill              40.748303              -73.978332   
17          Murray Hill              40.748303              -73.978332   
18          Murray Hill              40.748303              -73.978332   
19          Murray Hill              40.748303              -73.978332   
20              Chelsea              40.744035              -74.003116   
21              Chelsea              40.744035              -74.003116   
22              Chelsea              40.744035              -74.003116   
23              Chelsea              40.744035              -74.003116   
24              Chelsea              40.744035              -74.003116   
25         East Village              40.727847              -73.982226   
26         East Village              40.727847              -73.982226   
27         East Village              40.727847              -73.982226   
28              Tribeca              40.721522              -74.010683   
29              Tribeca              40.721522              -74.010683   
30  Morningside Heights              40.808000              -73.963896   
31  Morningside Heights              40.808000              -73.963896   
32    Battery Park City              40.711932              -74.016869   
33    Battery Park City              40.711932              -74.016869   
34    Battery Park City              40.711932              -74.016869   
35         Civic Center              40.715229              -74.005415   
36         Civic Center              40.715229              -74.005415   
37         Civic Center              40.715229              -74.005415   
38         Civic Center              40.715229              -74.005415   
39         Civic Center              40.715229              -74.005415   
40         Civic Center              40.715229              -74.005415   
41        Midtown South              40.748510              -73.988713   
42        Midtown South              40.748510              -73.988713   
43        Midtown South              40.748510              -73.988713   
44         Sutton Place              40.760280              -73.963556   
45         Sutton Place              40.760280              -73.963556   
46           Turtle Bay              40.752042              -73.967708   
47           Turtle Bay              40.752042              -73.967708   
48           Turtle Bay              40.752042              -73.967708   
49           Tudor City              40.746917              -73.971219   
50         Hudson Yards              40.756658              -74.000111   
51         Hudson Yards              40.756658              -74.000111   

                          Venue  Venue Latitude  Venue Longitude  \
0                   

In [70]:
Cluster1J = manhattan_venues_coffee.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster1J                                           

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Marble Hill              40.876551              -73.910660   
1             Chinatown              40.715618              -73.994279   
2        Manhattanville              40.816934              -73.957385   
3        Manhattanville              40.816934              -73.957385   
4        Lincoln Square              40.773529              -73.985338   
5        Lincoln Square              40.773529              -73.985338   
6               Clinton              40.759101              -73.996119   
7               Clinton              40.759101              -73.996119   
8               Clinton              40.759101              -73.996119   
9               Clinton              40.759101              -73.996119   
10              Clinton              40.759101              -73.996119   
11              Clinton              40.759101              -73.996119   
12              Midtown              40.754691              -73.981669   
13              Midtown              40.754691              -73.981669   
14              Midtown              40.754691              -73.981669   
15          Murray Hill              40.748303              -73.978332   
16          Murray Hill              40.748303              -73.978332   
17          Murray Hill              40.748303              -73.978332   
18          Murray Hill              40.748303              -73.978332   
19          Murray Hill              40.748303              -73.978332   
20              Chelsea              40.744035              -74.003116   
21              Chelsea              40.744035              -74.003116   
22              Chelsea              40.744035              -74.003116   
23              Chelsea              40.744035              -74.003116   
24              Chelsea              40.744035              -74.003116   
25         East Village              40.727847              -73.982226   
26         East Village              40.727847              -73.982226   
27         East Village              40.727847              -73.982226   
28              Tribeca              40.721522              -74.010683   
29              Tribeca              40.721522              -74.010683   
30  Morningside Heights              40.808000              -73.963896   
31  Morningside Heights              40.808000              -73.963896   
32    Battery Park City              40.711932              -74.016869   
33    Battery Park City              40.711932              -74.016869   
34    Battery Park City              40.711932              -74.016869   
35         Civic Center              40.715229              -74.005415   
36         Civic Center              40.715229              -74.005415   
37         Civic Center              40.715229              -74.005415   
38         Civic Center              40.715229              -74.005415   
39         Civic Center              40.715229              -74.005415   
40         Civic Center              40.715229              -74.005415   
41        Midtown South              40.748510              -73.988713   
42        Midtown South              40.748510              -73.988713   
43        Midtown South              40.748510              -73.988713   
44         Sutton Place              40.760280              -73.963556   
45         Sutton Place              40.760280              -73.963556   
46           Turtle Bay              40.752042              -73.967708   
47           Turtle Bay              40.752042              -73.967708   
48           Turtle Bay              40.752042              -73.967708   
49           Tudor City              40.746917              -73.971219   
50         Hudson Yards              40.756658              -74.000111   
51         Hudson Yards              40.756658              -74.000111   

                          Venue  Venue Latitude  Venue Longitude  \
0                   

Let's drop row 3 with no rating

In [71]:
Cluster1J = Cluster1J.drop(Cluster1J.index[3]).reset_index(drop=True)
Cluster1J

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Marble Hill              40.876551              -73.910660   
1             Chinatown              40.715618              -73.994279   
2        Manhattanville              40.816934              -73.957385   
3        Lincoln Square              40.773529              -73.985338   
4        Lincoln Square              40.773529              -73.985338   
5               Clinton              40.759101              -73.996119   
6               Clinton              40.759101              -73.996119   
7               Clinton              40.759101              -73.996119   
8               Clinton              40.759101              -73.996119   
9               Clinton              40.759101              -73.996119   
10              Clinton              40.759101              -73.996119   
11              Midtown              40.754691              -73.981669   
12              Midtown              40.754691              -73.981669   
13              Midtown              40.754691              -73.981669   
14          Murray Hill              40.748303              -73.978332   
15          Murray Hill              40.748303              -73.978332   
16          Murray Hill              40.748303              -73.978332   
17          Murray Hill              40.748303              -73.978332   
18          Murray Hill              40.748303              -73.978332   
19              Chelsea              40.744035              -74.003116   
20              Chelsea              40.744035              -74.003116   
21              Chelsea              40.744035              -74.003116   
22              Chelsea              40.744035              -74.003116   
23              Chelsea              40.744035              -74.003116   
24         East Village              40.727847              -73.982226   
25         East Village              40.727847              -73.982226   
26         East Village              40.727847              -73.982226   
27              Tribeca              40.721522              -74.010683   
28              Tribeca              40.721522              -74.010683   
29  Morningside Heights              40.808000              -73.963896   
30  Morningside Heights              40.808000              -73.963896   
31    Battery Park City              40.711932              -74.016869   
32    Battery Park City              40.711932              -74.016869   
33    Battery Park City              40.711932              -74.016869   
34         Civic Center              40.715229              -74.005415   
35         Civic Center              40.715229              -74.005415   
36         Civic Center              40.715229              -74.005415   
37         Civic Center              40.715229              -74.005415   
38         Civic Center              40.715229              -74.005415   
39         Civic Center              40.715229              -74.005415   
40        Midtown South              40.748510              -73.988713   
41        Midtown South              40.748510              -73.988713   
42        Midtown South              40.748510              -73.988713   
43         Sutton Place              40.760280              -73.963556   
44         Sutton Place              40.760280              -73.963556   
45           Turtle Bay              40.752042              -73.967708   
46           Turtle Bay              40.752042              -73.967708   
47           Turtle Bay              40.752042              -73.967708   
48           Tudor City              40.746917              -73.971219   
49         Hudson Yards              40.756658              -74.000111   
50         Hudson Yards              40.756658              -74.000111   

                          Venue  Venue Latitude  Venue Longitude  \
0                     Starbucks       40.877531       -73.905582   
1                  Little 

Let's find the mean for the Ratings column

In [72]:
Cluster1J["Rating"].mean()

7.9686274509803905

We will do the same for the other 4 Clusters

Manhattan Cluster 2

In [73]:
Cluster2 = manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]
Cluster2

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8      Upper East Side    Italian Restaurant               Exhibit   
9            Yorkville    Italian Restaurant      Sushi Restaurant   
10          Lenox Hill    Italian Restaurant                  Café   
12     Upper West Side    Italian Restaurant                Bakery   
18   Greenwich Village    Italian Restaurant        Clothing Store   
22        Little Italy                Bakery    Italian Restaurant   
23                Soho        Clothing Store    Italian Restaurant   
24        West Village    Italian Restaurant          Cocktail Bar   
27            Gramercy    Italian Restaurant           Pizza Place   
29  Financial District           Coffee Shop           Pizza Place   
30       Carnegie Hill           Coffee Shop             Wine Shop   
31                Noho    Italian Restaurant          Cocktail Bar   
38            Flatiron    Italian Restaurant                   Spa   

   3rd Most Common Venue    4th Most Common Venue    5th Most Common Venue  \
8                 Bakery                      Spa              Coffee Shop   
9            Coffee Shop      Japanese Restaurant                      Gym   
10           Pizza Place         Sushi Restaurant                     Bank   
12              Wine Bar                     Café              Coffee Shop   
18      Sushi Restaurant             Dessert Shop        Indian Restaurant   
22                  Café              Coffee Shop           Sandwich Place   
23            Shoe Store                 Boutique            Women's Store   
24                  Park  New American Restaurant                 Wine Bar   
27        Sandwich Place              Coffee Shop       Mexican Restaurant   
29  Gym / Fitness Center             Cocktail Bar       Falafel Restaurant   
30           Pizza Place           Cosmetics Shop                      Gym   
31           Pizza Place            Grocery Store         Sushi Restaurant   
38   American Restaurant      Japanese Restaurant  New American Restaurant   

   6th Most Common Venue      7th Most Common Venue     8th Most Common Venue  \
8              Juice Bar                Yoga Studio       American Restaurant   
9                  Diner                        Bar             Deli / Bodega   
10  Gym / Fitness Center               Burger Joint             Deli / Bodega   
12        Ice Cream Shop  Middle Eastern Restaurant         Indian Restaurant   
18                  Café                Coffee Shop         Accessories Store   
22                   Spa                   Tea Room               Pizza Place   
23                Bakery               Dessert Shop               Coffee Shop   
24   American Restaurant                  Jazz Club               Coffee Shop   
27            Bagel Shop                 Taco Place                      Park   
29   American Restaurant                 Steakhouse                      Café   
30                  Café                Yoga Studio                Art Museum   
31              Wine Bar                      Hotel                 Bookstore   
38             Wine Shop       Gym / Fitness Center  Mediterranean Restaurant   

   9th Most Common Venue    10th Most Common Venue  
8                  Hotel                 Wine Shop  
9                   Park                       Spa  
10          Cocktail Bar                       Gym  
12           Pizza Place       American Restaurant  
18    Seafood Restaurant               Pizza Place  
22        Ice Cream Shop        Salon / Barbershop  
23    Salon / Barbershop  Mediterranean Restaurant  
24    Seafood Restaurant            Sandwich Place  
27                 Diner                       Spa  
29                   Gym                Donut Shop  
30   Japanese Restaurant      Gym / Fitness Center  
31           Coffee Shop       Japanese Restaurant  
38           Coffee Shop              Dessert Shop

In [75]:
Cluster1_Neighborhood = Cluster2['Neighborhood'].reset_index(drop=True)
Cluster1_Neighborhood

0        Upper East Side
1              Yorkville
2             Lenox Hill
3        Upper West Side
4      Greenwich Village
5           Little Italy
6                   Soho
7           West Village
8               Gramercy
9     Financial District
10         Carnegie Hill
11                  Noho
12              Flatiron
Name: Neighborhood, dtype: object

In [76]:
manhattan_venues_coffee2 = manhattan_venues[(manhattan_venues['Neighborhood'].str.contains("Upper East Side|Yorkville|Lenox Hill|Upper West Side|Greenwich Village|Little Italy|Soho|West Village|Gramercy|Financial District|Carnegie Hill|Noho|Flatiron")) & (manhattan_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
manhattan_venues_coffee2

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Upper East Side              40.775639              -73.960508   
1      Upper East Side              40.775639              -73.960508   
2      Upper East Side              40.775639              -73.960508   
3            Yorkville              40.775930              -73.947118   
4            Yorkville              40.775930              -73.947118   
5            Yorkville              40.775930              -73.947118   
6            Yorkville              40.775930              -73.947118   
7            Yorkville              40.775930              -73.947118   
8           Lenox Hill              40.768113              -73.958860   
9           Lenox Hill              40.768113              -73.958860   
10          Lenox Hill              40.768113              -73.958860   
11     Upper West Side              40.787658              -73.977059   
12     Upper West Side              40.787658              -73.977059   
13     Upper West Side              40.787658              -73.977059   
14   Greenwich Village              40.726933              -73.999914   
15   Greenwich Village              40.726933              -73.999914   
16   Greenwich Village              40.726933              -73.999914   
17        Little Italy              40.719324              -73.997305   
18        Little Italy              40.719324              -73.997305   
19        Little Italy              40.719324              -73.997305   
20                Soho              40.722184              -74.000657   
21                Soho              40.722184              -74.000657   
22                Soho              40.722184              -74.000657   
23        West Village              40.734434              -74.006180   
24        West Village              40.734434              -74.006180   
25        West Village              40.734434              -74.006180   
26            Gramercy              40.737210              -73.981376   
27            Gramercy              40.737210              -73.981376   
28            Gramercy              40.737210              -73.981376   
29  Financial District              40.707107              -74.010665   
30  Financial District              40.707107              -74.010665   
31  Financial District              40.707107              -74.010665   
32  Financial District              40.707107              -74.010665   
33  Financial District              40.707107              -74.010665   
34  Financial District              40.707107              -74.010665   
35  Financial District              40.707107              -74.010665   
36  Financial District              40.707107              -74.010665   
37  Financial District              40.707107              -74.010665   
38       Carnegie Hill              40.782683              -73.953256   
39       Carnegie Hill              40.782683              -73.953256   
40       Carnegie Hill              40.782683              -73.953256   
41       Carnegie Hill              40.782683              -73.953256   
42       Carnegie Hill              40.782683              -73.953256   
43                Noho              40.723259              -73.988434   
44                Noho              40.723259              -73.988434   
45                Noho              40.723259              -73.988434   
46            Flatiron              40.739673              -73.990947   
47            Flatiron              40.739673              -73.990947   
48            Flatiron              40.739673              -73.990947   

                             Venue  Venue Latitude  Venue Longitude  \
0                 Handcraft Coffee       40.773535       -73.959670   
1            Joe the Art of Coffee       40.772044       -73.960805   
2                        Nespresso       40.773179       -73.964406   
3                     Stella & Fly       40.778464       -73.948282   
4   

In [77]:
Cluster2J = manhattan_venues_coffee2.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster2J  

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Upper East Side              40.775639              -73.960508   
1      Upper East Side              40.775639              -73.960508   
2      Upper East Side              40.775639              -73.960508   
3            Yorkville              40.775930              -73.947118   
4            Yorkville              40.775930              -73.947118   
5            Yorkville              40.775930              -73.947118   
6            Yorkville              40.775930              -73.947118   
7            Yorkville              40.775930              -73.947118   
8           Lenox Hill              40.768113              -73.958860   
9           Lenox Hill              40.768113              -73.958860   
10          Lenox Hill              40.768113              -73.958860   
11     Upper West Side              40.787658              -73.977059   
12     Upper West Side              40.787658              -73.977059   
13     Upper West Side              40.787658              -73.977059   
14   Greenwich Village              40.726933              -73.999914   
15   Greenwich Village              40.726933              -73.999914   
16   Greenwich Village              40.726933              -73.999914   
17        Little Italy              40.719324              -73.997305   
18        Little Italy              40.719324              -73.997305   
19        Little Italy              40.719324              -73.997305   
20                Soho              40.722184              -74.000657   
21                Soho              40.722184              -74.000657   
22                Soho              40.722184              -74.000657   
23        West Village              40.734434              -74.006180   
24        West Village              40.734434              -74.006180   
25        West Village              40.734434              -74.006180   
26            Gramercy              40.737210              -73.981376   
27            Gramercy              40.737210              -73.981376   
28            Gramercy              40.737210              -73.981376   
29  Financial District              40.707107              -74.010665   
30  Financial District              40.707107              -74.010665   
31  Financial District              40.707107              -74.010665   
32  Financial District              40.707107              -74.010665   
33  Financial District              40.707107              -74.010665   
34  Financial District              40.707107              -74.010665   
35  Financial District              40.707107              -74.010665   
36  Financial District              40.707107              -74.010665   
37  Financial District              40.707107              -74.010665   
38       Carnegie Hill              40.782683              -73.953256   
39       Carnegie Hill              40.782683              -73.953256   
40       Carnegie Hill              40.782683              -73.953256   
41       Carnegie Hill              40.782683              -73.953256   
42       Carnegie Hill              40.782683              -73.953256   
43                Noho              40.723259              -73.988434   
44                Noho              40.723259              -73.988434   
45                Noho              40.723259              -73.988434   
46            Flatiron              40.739673              -73.990947   
47            Flatiron              40.739673              -73.990947   
48            Flatiron              40.739673              -73.990947   

                             Venue  Venue Latitude  Venue Longitude  \
0                 Handcraft Coffee       40.773535       -73.959670   
1            Joe the Art of Coffee       40.772044       -73.960805   
2                        Nespresso       40.773179       -73.964406   
3                     Stella & Fly       40.778464       -73.948282   
4   

In [78]:
Cluster2J["Rating"].mean()

8.179591836734692

Manhattan Cluster 3

In [79]:
Cluster3 = manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]
Cluster3

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
11  Roosevelt Island           Coffee Shop                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11         Deli / Bodega           Supermarket         Metro Station   

   6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
11        Farmers Market  Outdoors & Recreation          Soccer Field   

   9th Most Common Venue 10th Most Common Venue  
11                   Gym   Gym / Fitness Center

In [80]:
manhattan_venues_coffee3 = manhattan_venues[(manhattan_venues['Neighborhood'].str.contains("Roosevelt Island")) & (manhattan_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
manhattan_venues_coffee3

Neighborhood  Neighborhood Latitude  Neighborhood Longitude      Venue  \
0  Roosevelt Island               40.76216              -73.949168  Starbucks   
1  Roosevelt Island               40.76216              -73.949168  Starbucks   

   Venue Latitude  Venue Longitude                  Venue ID Venue Category  
0        40.76498       -73.953124  599f1eb6fd16bb4a5da9d3f9    Coffee Shop  
1        40.75936       -73.953153  4b0807abf964a520890223e3    Coffee Shop

In [81]:
Cluster3J = manhattan_venues_coffee3.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster3J 

Neighborhood  Neighborhood Latitude  Neighborhood Longitude      Venue  \
0  Roosevelt Island               40.76216              -73.949168  Starbucks   
1  Roosevelt Island               40.76216              -73.949168  Starbucks   

   Venue Latitude  Venue Longitude                  Venue ID Venue Category  \
0        40.76498       -73.953124  599f1eb6fd16bb4a5da9d3f9    Coffee Shop   
1        40.75936       -73.953153  4b0807abf964a520890223e3    Coffee Shop   

   Rating  
0     7.1  
1     6.0

In [82]:
Cluster3J["Rating"].mean()

6.55

Manhattan Cluster 4

In [83]:
Cluster4 = manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]
Cluster4

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town         Boat or Ferry                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37           Yoga Studio           Pet Service              Fountain   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37                Bistro       Harbor / Marina          Cocktail Bar   

   9th Most Common Venue 10th Most Common Venue  
37              Heliport            Coffee Shop

In [84]:
manhattan_venues_coffee4 = manhattan_venues[(manhattan_venues['Neighborhood'].str.contains("Stuyvesant Town")) & (manhattan_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
manhattan_venues_coffee4

Neighborhood  Neighborhood Latitude  Neighborhood Longitude       Venue  \
0  Stuyvesant Town                 40.731              -73.974052  B Cup Cafe   

   Venue Latitude  Venue Longitude                  Venue ID Venue Category  
0       40.728783       -73.978565  457bd9adf964a520f63e1fe3    Coffee Shop

In [85]:
Cluster4J = manhattan_venues_coffee4.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster4J 

Neighborhood  Neighborhood Latitude  Neighborhood Longitude       Venue  \
0  Stuyvesant Town                 40.731              -73.974052  B Cup Cafe   

   Venue Latitude  Venue Longitude                  Venue ID Venue Category  \
0       40.728783       -73.978565  457bd9adf964a520f63e1fe3    Coffee Shop   

   Rating  
0     7.5

In [86]:
Cluster4J["Rating"].mean()

7.5

Manhattan Cluster 5

In [87]:
Cluster5 = manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]
Cluster5

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2   Washington Heights                  Café         Grocery Store   
3               Inwood    Mexican Restaurant                Lounge   
4     Hamilton Heights           Pizza Place    Mexican Restaurant   
7          East Harlem           Pizza Place                Bakery   
20     Lower East Side           Pizza Place        Sandwich Place   
25    Manhattan Valley           Yoga Studio                   Bar   

   3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
2            Pizza Place    Chinese Restaurant      Mobile Phone Shop   
3                   Café                  Park                 Bakery   
4                   Café        Sandwich Place            Yoga Studio   
7     Mexican Restaurant                   Spa         Sandwich Place   
20                  Café    Chinese Restaurant            Art Gallery   
25     Indian Restaurant           Coffee Shop  Vietnamese Restaurant   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
2                   Bank                Bakery               Pharmacy   
3                   Bank         Deli / Bodega   Caribbean Restaurant   
4           Cocktail Bar                Bakery      Mobile Phone Shop   
7             Steakhouse                  Bank       Cuban Restaurant   
20                Bakery          Dance Studio  Performing Arts Venue   
25    Mexican Restaurant            Playground            Pizza Place   

        9th Most Common Venue   10th Most Common Venue  
2          Spanish Restaurant         Tapas Restaurant  
3                    Wine Bar              Pizza Place  
4   Latin American Restaurant     Caribbean Restaurant  
7              Clothing Store  New American Restaurant  
20                       Park                 Pet Café  
25       Ethiopian Restaurant          Bubble Tea Shop

In [88]:
manhattan_venues_coffee5 = manhattan_venues[(manhattan_venues['Neighborhood'].str.contains("Inwood|Washington Heights|Hamilton Heights|East Harlem|Lower East Side|Manhattan Valley")) & (manhattan_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
manhattan_venues_coffee5

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Washington Heights              40.851903              -73.936900   
1  Washington Heights              40.851903              -73.936900   
2              Inwood              40.867684              -73.921210   
3    Hamilton Heights              40.823604              -73.949688   
4    Manhattan Valley              40.797307              -73.964286   
5    Manhattan Valley              40.797307              -73.964286   

                            Venue  Venue Latitude  Venue Longitude  \
0              Forever Coffee Bar       40.850433       -73.936607   
1                       Starbucks       40.850961       -73.938330   
2                      Kuro Kirin       40.866223       -73.925691   
3                      Monkey Cup       40.825694       -73.947234   
4                   Peaky Barista       40.798568       -73.968577   
5  Plowshares Coffee Bloomingdale       40.800191       -73.968066   

                   Venue ID Venue Category  
0  5bafd8419de23b002c772a72    Coffee Shop  
1  4aafdf93f964a520f66420e3    Coffee Shop  
2  5c092ec2d1a402002cd083cb    Coffee Shop  
3  55aa54bc498eac980f832bc9    Coffee Shop  
4  5d864371ebc5f80008c24794    Coffee Shop  
5  54733f59498e78d5fb3a0755    Coffee Shop

In [89]:
Cluster5J = manhattan_venues_coffee5.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster5J 

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Washington Heights              40.851903              -73.936900   
1  Washington Heights              40.851903              -73.936900   
2              Inwood              40.867684              -73.921210   
3    Hamilton Heights              40.823604              -73.949688   
4    Manhattan Valley              40.797307              -73.964286   
5    Manhattan Valley              40.797307              -73.964286   

                            Venue  Venue Latitude  Venue Longitude  \
0              Forever Coffee Bar       40.850433       -73.936607   
1                       Starbucks       40.850961       -73.938330   
2                      Kuro Kirin       40.866223       -73.925691   
3                      Monkey Cup       40.825694       -73.947234   
4                   Peaky Barista       40.798568       -73.968577   
5  Plowshares Coffee Bloomingdale       40.800191       -73.968066   

                   Venue ID Venue Category  Rating  
0  5bafd8419de23b002c772a72    Coffee Shop     8.0  
1  4aafdf93f964a520f66420e3    Coffee Shop     6.4  
2  5c092ec2d1a402002cd083cb    Coffee Shop     8.2  
3  55aa54bc498eac980f832bc9    Coffee Shop     8.0  
4  5d864371ebc5f80008c24794    Coffee Shop     8.0  
5  54733f59498e78d5fb3a0755    Coffee Shop     7.7

In [90]:
Cluster5J["Rating"].mean()

7.716666666666668

Let's summerize the results

In [205]:
data =[['Cluster1', Cluster1J["Rating"].mean(),len(Cluster1J.index)], 
      ['Cluster2', Cluster2J["Rating"].mean(),len(Cluster2J.index)],
      ['Cluster3', Cluster3J["Rating"].mean(),len(Cluster3J.index)],
      ['Cluster4', Cluster4J["Rating"].mean(),len(Cluster4J.index)],
      ['Cluster5', Cluster5J["Rating"].mean(),len(Cluster5J.index)]] 

dfm = pd.DataFrame(data, columns = ['Manhattan Cluster', 'Mean', 'Amount of Coffee Shops'])
dfm

Manhattan Cluster      Mean  Amount of Coffee Shops
0          Cluster1  7.968627                      51
1          Cluster2  8.179592                      49
2          Cluster3  6.550000                       2
3          Cluster4  7.500000                       1
4          Cluster5  7.716667                       6

Now we will need to do the same for Toronto.

In [96]:
from bs4 import BeautifulSoup # this module helps in web scrapping.
import requests  # this module helps us to download a web page

print('Libraries imported.')

Libraries imported.


Scraping Wikipedio for data

In [97]:
#asinging url, converting to txt and using BeatifulSoup
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
data = requests.get(url).text
soup = BeautifulSoup(data,"html5lib")
#find all html tables in the web page
tables = soup.find_all('table') # in html table is represented by the tag <table>

In [98]:
#looking how many tables are in an url
len(tables)

3

In [99]:
#Finding table number with post code
for index,table in enumerate(tables):
    if ("M1A" in str(table)):
        table_index = index
print(table_index)

0


In [100]:
#getting data to a table and cleaning it
table_contents = []
table=soup.find('table')
for row in tables[table_index].tbody.find_all('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['PostalCode'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_contents.append(cell)

# print(table_contents) and cleaning data
df=pd.DataFrame(table_contents)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})

In [101]:
#looking into the result
df

PostalCode                 Borough  \
0          M3A              North York   
1          M4A              North York   
2          M5A        Downtown Toronto   
3          M6A              North York   
4          M7A            Queen's Park   
5          M9A               Etobicoke   
6          M1B             Scarborough   
7          M3B              North York   
8          M4B               East York   
9          M5B        Downtown Toronto   
10         M6B              North York   
11         M9B               Etobicoke   
12         M1C             Scarborough   
13         M3C              North York   
14         M4C               East York   
15         M5C        Downtown Toronto   
16         M6C                    York   
17         M9C               Etobicoke   
18         M1E             Scarborough   
19         M4E            East Toronto   
20         M5E        Downtown Toronto   
21         M6E                    York   
22         M1G             Scarborough   
23         M4G               East York   
24         M5G        Downtown Toronto   
25         M6G        Downtown Toronto   
26         M1H             Scarborough   
27         M2H              North York   
28         M3H              North York   
29         M4H               East York   
30         M5H        Downtown Toronto   
31         M6H            West Toronto   
32         M1J             Scarborough   
33         M2J              North York   
34         M3J              North York   
35         M4J  East York/East Toronto   
36         M5J        Downtown Toronto   
37         M6J            West Toronto   
38         M1K             Scarborough   
39         M2K              North York   
40         M3K              North York   
41         M4K            East Toronto   
42         M5K        Downtown Toronto   
43         M6K            West Toronto   
44         M1L             Scarborough   
45         M2L              North York   
46         M3L              North York   
47         M4L            East Toronto   
48         M5L        Downtown Toronto   
49         M6L              North York   
50         M9L              North York   
51         M1M             Scarborough   
52         M2M              North York   
53         M3M              North York   
54         M4M            East Toronto   
55         M5M              North York   
56         M6M                    York   
57         M9M              North York   
58         M1N             Scarborough   
59         M2N              North York   
60         M3N              North York   
61         M4N         Central Toronto   
62         M5N         Central Toronto   
63         M6N                    York   
64         M9N                    York   
65         M1P             Scarborough   
66         M2P              North York   
67         M4P         Central Toronto   
68         M5P         Central Toronto   
69         M6P            West Toronto   
70         M9P               Etobicoke   
71         M1R             Scarborough   
72         M2R              North York   
73         M4R         Central Toronto   
74         M5R         Central Toronto   
75         M6R            West Toronto   
76         M7R             Mississauga   
77         M9R               Etobicoke   
78         M1S             Scarborough   
79         M4S         Central Toronto   
80         M5S        Downtown Toronto   
81         M6S            West Toronto   
82         M1T             Scarborough   
83         M4T         Central Toronto   
84         M5T        Downtown Toronto   
85         M1V             Scarborough   
86         M4V         Central Toronto   
87         M5V        Downtown Toronto   
88         M8V               Etobicoke   
89         M9V               Etobicoke   
90         M1W             Scarborough   
91         M4W        Downtown Toronto   
92         M5W  Downtown Toronto Stn A   
93         M8W               Etobicoke   
94         M9W

In [102]:
#shape of dataframe
df.shape

(103, 3)

Importing Latitude and Longitude from csv file.

In [103]:
url2 = 'https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs_v1/Geospatial_Coordinates.csv'

In [104]:
df2=pd.read_csv(url2)
df2

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
5           M1J  43.744734 -79.239476
6           M1K  43.727929 -79.262029
7           M1L  43.711112 -79.284577
8           M1M  43.716316 -79.239476
9           M1N  43.692657 -79.264848
10          M1P  43.757410 -79.273304
11          M1R  43.750072 -79.295849
12          M1S  43.794200 -79.262029
13          M1T  43.781638 -79.304302
14          M1V  43.815252 -79.284577
15          M1W  43.799525 -79.318389
16          M1X  43.836125 -79.205636
17          M2H  43.803762 -79.363452
18          M2J  43.778517 -79.346556
19          M2K  43.786947 -79.385975
20          M2L  43.757490 -79.374714
21          M2M  43.789053 -79.408493
22          M2N  43.770120 -79.408493
23          M2P  43.752758 -79.400049
24          M2R  43.782736 -79.442259
25          M3A  43.753259 -79.329656
26          M3B  43.745906 -79.352188
27          M3C  43.725900 -79.340923
28          M3H  43.754328 -79.442259
29          M3J  43.767980 -79.487262
30          M3K  43.737473 -79.464763
31          M3L  43.739015 -79.506944
32          M3M  43.728496 -79.495697
33          M3N  43.761631 -79.520999
34          M4A  43.725882 -79.315572
35          M4B  43.706397 -79.309937
36          M4C  43.695344 -79.318389
37          M4E  43.676357 -79.293031
38          M4G  43.709060 -79.363452
39          M4H  43.705369 -79.349372
40          M4J  43.685347 -79.338106
41          M4K  43.679557 -79.352188
42          M4L  43.668999 -79.315572
43          M4M  43.659526 -79.340923
44          M4N  43.728020 -79.388790
45          M4P  43.712751 -79.390197
46          M4R  43.715383 -79.405678
47          M4S  43.704324 -79.388790
48          M4T  43.689574 -79.383160
49          M4V  43.686412 -79.400049
50          M4W  43.679563 -79.377529
51          M4X  43.667967 -79.367675
52          M4Y  43.665860 -79.383160
53          M5A  43.654260 -79.360636
54          M5B  43.657162 -79.378937
55          M5C  43.651494 -79.375418
56          M5E  43.644771 -79.373306
57          M5G  43.657952 -79.387383
58          M5H  43.650571 -79.384568
59          M5J  43.640816 -79.381752
60          M5K  43.647177 -79.381576
61          M5L  43.648198 -79.379817
62          M5M  43.733283 -79.419750
63          M5N  43.711695 -79.416936
64          M5P  43.696948 -79.411307
65          M5R  43.672710 -79.405678
66          M5S  43.662696 -79.400049
67          M5T  43.653206 -79.400049
68          M5V  43.628947 -79.394420
69          M5W  43.646435 -79.374846
70          M5X  43.648429 -79.382280
71          M6A  43.718518 -79.464763
72          M6B  43.709577 -79.445073
73          M6C  43.693781 -79.428191
74          M6E  43.689026 -79.453512
75          M6G  43.669542 -79.422564
76          M6H  43.669005 -79.442259
77          M6J  43.647927 -79.419750
78          M6K  43.636847 -79.428191
79          M6L  43.713756 -79.490074
80          M6M  43.691116 -79.476013
81          M6N  43.673185 -79.487262
82          M6P  43.661608 -79.464763
83          M6R  43.648960 -79.456325
84          M6S  43.651571 -79.484450
85          M7A  43.662301 -79.389494
86          M7R  43.636966 -79.615819
87          M7Y  43.662744 -79.321558
88          M8V  43.605647 -79.501321
89          M8W  43.602414 -79.543484
90          M8X  43.653654 -79.506944
91          M8Y  43.636258 -79.498509
92          M8Z  43.628841 -79.520999
93          M9A  43.667856 -79.532242
94          M9B  43.650943 -79.554724
95          M9C  43.643515 -79.577201
96          M9L  43.756303 -79.565963
97          M9M  43.724766 -79.532242
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

In [105]:
df2.shape

(103, 3)

Merging both dataframes

In [106]:
Toronto_data = df.join(df2.set_index('Postal Code'), on='PostalCode')
Toronto_data

PostalCode                 Borough  \
0          M3A              North York   
1          M4A              North York   
2          M5A        Downtown Toronto   
3          M6A              North York   
4          M7A            Queen's Park   
5          M9A               Etobicoke   
6          M1B             Scarborough   
7          M3B              North York   
8          M4B               East York   
9          M5B        Downtown Toronto   
10         M6B              North York   
11         M9B               Etobicoke   
12         M1C             Scarborough   
13         M3C              North York   
14         M4C               East York   
15         M5C        Downtown Toronto   
16         M6C                    York   
17         M9C               Etobicoke   
18         M1E             Scarborough   
19         M4E            East Toronto   
20         M5E        Downtown Toronto   
21         M6E                    York   
22         M1G             Scarborough   
23         M4G               East York   
24         M5G        Downtown Toronto   
25         M6G        Downtown Toronto   
26         M1H             Scarborough   
27         M2H              North York   
28         M3H              North York   
29         M4H               East York   
30         M5H        Downtown Toronto   
31         M6H            West Toronto   
32         M1J             Scarborough   
33         M2J              North York   
34         M3J              North York   
35         M4J  East York/East Toronto   
36         M5J        Downtown Toronto   
37         M6J            West Toronto   
38         M1K             Scarborough   
39         M2K              North York   
40         M3K              North York   
41         M4K            East Toronto   
42         M5K        Downtown Toronto   
43         M6K            West Toronto   
44         M1L             Scarborough   
45         M2L              North York   
46         M3L              North York   
47         M4L            East Toronto   
48         M5L        Downtown Toronto   
49         M6L              North York   
50         M9L              North York   
51         M1M             Scarborough   
52         M2M              North York   
53         M3M              North York   
54         M4M            East Toronto   
55         M5M              North York   
56         M6M                    York   
57         M9M              North York   
58         M1N             Scarborough   
59         M2N              North York   
60         M3N              North York   
61         M4N         Central Toronto   
62         M5N         Central Toronto   
63         M6N                    York   
64         M9N                    York   
65         M1P             Scarborough   
66         M2P              North York   
67         M4P         Central Toronto   
68         M5P         Central Toronto   
69         M6P            West Toronto   
70         M9P               Etobicoke   
71         M1R             Scarborough   
72         M2R              North York   
73         M4R         Central Toronto   
74         M5R         Central Toronto   
75         M6R            West Toronto   
76         M7R             Mississauga   
77         M9R               Etobicoke   
78         M1S             Scarborough   
79         M4S         Central Toronto   
80         M5S        Downtown Toronto   
81         M6S            West Toronto   
82         M1T             Scarborough   
83         M4T         Central Toronto   
84         M5T        Downtown Toronto   
85         M1V             Scarborough   
86         M4V         Central Toronto   
87         M5V        Downtown Toronto   
88         M8V               Etobicoke   
89         M9V               Etobicoke   
90         M1W             Scarborough   
91         M4W        Downtown Toronto   
92         M5W  Downtown Toronto Stn A   
93         M8W               Etobicoke   
94         M9W

Finding Toronto geograpical coordinates

In [107]:
address = 'Toronto'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


Creating a map of Toronto with Neighborhood data

In [108]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(Toronto_data['Latitude'], Toronto_data['Longitude'], Toronto_data['Borough'], Toronto_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

We will focus on the central part of Toronto. For this we will find all Boroughs with name Toronto in them.

In [109]:
Toronto_data2 = Toronto_data[Toronto_data['Borough'].str.contains("Toronto")].reset_index(drop=True)
Toronto_data2.head()

PostalCode           Borough               Neighborhood   Latitude  \
0        M5A  Downtown Toronto  Regent Park, Harbourfront  43.654260   
1        M5B  Downtown Toronto   Garden District, Ryerson  43.657162   
2        M5C  Downtown Toronto             St. James Town  43.651494   
3        M4E      East Toronto                The Beaches  43.676357   
4        M5E  Downtown Toronto                Berczy Park  43.644771   

   Longitude  
0 -79.360636  
1 -79.378937  
2 -79.375418  
3 -79.293031  
4 -79.373306

Creating the same map with filtered Boroughs

In [110]:
# create map of Toronto (Borough = Toronto) using latitude and longitude values
map_toronto2 = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(Toronto_data2['Latitude'], Toronto_data2['Longitude'], Toronto_data2['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto2)  
    
map_toronto2

Create a function to process all the neighborhoods and get nearby venues

In [1]:
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            500, 
            LIMIT)

NameError: name 'CLIENT_ID' is not defined

In [128]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],
            v['venue']['id'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude',
                  'Venue ID',          
                  'Venue Category']
    
    return(nearby_venues)

Run thorugh all neighborhood and create a new dataframe called Toronto_venues

In [129]:
Toronto_venues = getNearbyVenues(names=Toronto_data2['Neighborhood'],
                                   latitudes=Toronto_data2['Latitude'],
                                   longitudes=Toronto_data2['Longitude']
                                  )

Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Dufferin, Dovercourt Village
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
The Danforth West, Riverdale
Toronto Dominion Centre, Design Exchange
Brockton, Parkdale Village, Exhibition Place
India Bazaar, The Beaches West
Commerce Court, Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North & West
High Park, The Junction South
North Toronto West
The Annex, North Midtown, Yorkville
Parkdale, Roncesvalles
Davisville
University of Toronto, Harbord
Runnymede, Swansea
Moore Park, Summerhill East
Kensington Market, Chinatown, Grange Park
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Rosedale
Enclave of M5E
St. James Town, Cabbagetown
First Canadi

Let's check the size of the resulting dataframe

In [130]:
print(Toronto_venues.shape)
Toronto_venues.head()

(1490, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront               43.65426              -79.360636   
1  Regent Park, Harbourfront               43.65426              -79.360636   
2  Regent Park, Harbourfront               43.65426              -79.360636   
3  Regent Park, Harbourfront               43.65426              -79.360636   
4  Regent Park, Harbourfront               43.65426              -79.360636   

                    Venue  Venue Latitude  Venue Longitude  \
0           Tandem Coffee       43.653559       -79.361809   
1        Roselle Desserts       43.653447       -79.362017   
2  Cooper Koo Family YMCA       43.653249       -79.358008   
3     Body Blitz Spa East       43.654735       -79.359874   
4          Impact Kitchen       43.656369       -79.356980   

                   Venue ID       Venue Category  
0  53b8466a498e83df908c3f21          Coffee Shop  
1  54ea41ad498e9a11e9e13308               Bakery  
2  574c229e498ebb5c6b257902  Distribution Center  
3  50760559e4b0e8c7babe2497                  Spa  
4  5612b1cc498e3dd742af0dc8           Restaurant

Now, we will find all coffie shops in the list and assing it to a new dataframe.

In [131]:
Toronto_rating = Toronto_venues[['Venue ID', 'Venue Category']]
Toronto_rating

Venue ID                   Venue Category
0     53b8466a498e83df908c3f21                      Coffee Shop
1     54ea41ad498e9a11e9e13308                           Bakery
2     574c229e498ebb5c6b257902              Distribution Center
3     50760559e4b0e8c7babe2497                              Spa
4     5612b1cc498e3dd742af0dc8                       Restaurant
5     4ad4c05ef964a520bff620e3                    Historic Site
6     4c3e1eaa6faac9b66dc60d76                   Farmers Market
7     4b0978e1f964a520cd1723e3                   Chocolate Shop
8     57cd9d20498e6ab8342980e2                      Coffee Shop
9     5619551a498e9e35fce2256b                      Coffee Shop
10    51853a73498e4d97a8b20831                      Coffee Shop
11    4c16a548955976b0cadea4f6                             Park
12    4bb68165f562ef3b88483097            Performing Arts Venue
13    4bc39c914cdfc9b6f29c9721                 Greek Restaurant
14    5653a96f498e99c91027730b                     Dessert Shop
15    4ddfbaca185035f3a44e8df6                             Park
16    4b156a02f964a5207fac23e3                           Bakery
17    5b7ccd5e1f8ed6002c9bd7d0                              Pub
18    4af59046f964a520e0f921e3                   Breakfast Spot
19    4ade8ea8f964a5205a7621e3                      Event Space
20    51ccc048498ec7792efc955e                             Park
21    4d126fd3d1848cfad5cfbb71                             Bank
22    58c7fbf7424f9373e6427e99                      Coffee Shop
23    4d84d98181fdb1f7d4a704c0                             Café
24    4bd8630535aad13a4bb890f3                   Sandwich Place
25    4ad4c05df964a5204ef620e3                           Bakery
26    4bb52a8bf562ef3b7d992e97                          Theater
27    566e1294498e3f6629006bc3                              Pub
28    53a22c92498ec91fda7ce133                French Restaurant
29    50e88fc6e4b007fcbb57aae8                 Asian Restaurant
30    581258b738fa5bbefe4c0857                      Coffee Shop
31    4af9fc95f964a520ca1522e3                              Pub
32    4af21e78f964a520fae521e3                      Art Gallery
33    4b8acdfdf964a520378232e3                       Beer Store
34    51ddecee498e1ffd34185d2f               Mexican Restaurant
35    4b2cf78cf964a52077cb24e3                      Coffee Shop
36    4ad8d551f964a5201f1521e3                Electronics Store
37    50a68e87e4b010802c0985e6                   Discount Store
38    54d37e23498e5e29bcb35362                             Café
39    593b5fbea35dce738ebbb4ec                            Hotel
40    5834fe851470b05200a49735                        Wine Shop
41    6043da90c2a0d03a5423b27f                             Café
42    579cc5f2498e0fe8397deebb                     Antique Shop
43    56d4d1b3cd1035fe77e1492c                             Café
44    5615b6c4498e3c32c67ad78f                      Pizza Place
45    4cd2e74d3e0c8cfa87971a12                             Café
46    4ad4c062f964a5200bf820e3                       Comic Shop
47    55a9bbf9498e00ffd7f4c71f                    Burrito Place
48    57eda381498ebe0e6ef40972                   Clothing Store
49    4ad750f0f964a5206f0921e3               Falafel Restaurant
50    514cc159e4b0e4f73af4eced                      Music Venue
51    568dcf20498e1601e2f8b87f        Middle Eastern Restaurant
52    51755dc7498ece19b7261641                   Sandwich Place
53    4ad8cd16f964a520c91421e3                            Plaza
54    5a81ae339deb7d369fa7f146                      Coffee Shop
55    539c6f13498e06f4cc765165       Modern European Restaurant
56    4ad4c062f964a520b5f720e3                          Theater
57    4b2bd898f964a52042bc24e3              Japanese Restaurant
58    4b7d9098f964a52014c72fe3                            Hotel
59    4afc79c8f964a520182322e3                   Clothing Store
60    4b32a8bdf964a5202d1125e3                       Steakhouse
61    55c294b0498e7ccb190b4bea                        

In [132]:
Toronto_rating2 = Toronto_rating[Toronto_rating['Venue Category'] == 'Coffee Shop'].reset_index(drop=True)
Toronto_rating2

Venue ID Venue Category
0    53b8466a498e83df908c3f21    Coffee Shop
1    57cd9d20498e6ab8342980e2    Coffee Shop
2    5619551a498e9e35fce2256b    Coffee Shop
3    51853a73498e4d97a8b20831    Coffee Shop
4    58c7fbf7424f9373e6427e99    Coffee Shop
5    581258b738fa5bbefe4c0857    Coffee Shop
6    4b2cf78cf964a52077cb24e3    Coffee Shop
7    5a81ae339deb7d369fa7f146    Coffee Shop
8    4b9e7418f964a52032e536e3    Coffee Shop
9    4bc3360374a9a593692ed4f6    Coffee Shop
10   4d077daee350b60c3bbb9242    Coffee Shop
11   4e9de9fbb803b7506dcf4c41    Coffee Shop
12   4fb13c20e4b011e6f93513c0    Coffee Shop
13   57d32c53498e983542aa781c    Coffee Shop
14   4af1939bf964a5206de121e3    Coffee Shop
15   4e776dd788775d593ed36897    Coffee Shop
16   4b7aa994f964a5200c362fe3    Coffee Shop
17   5a39970cc6666622a0eae5d0    Coffee Shop
18   565caeca498e1e36a503b42c    Coffee Shop
19   4b5219ccf964a520d56727e3    Coffee Shop
20   4fff1f96e4b042ae8acddca5    Coffee Shop
21   57963897498e6873394a559d    Coffee Shop
22   5b8431619f8a9f002c9bdc53    Coffee Shop
23   4dadd38a0cb6f003f490e329    Coffee Shop
24   54f9c6de498eb5e6895c94b2    Coffee Shop
25   4b619337f964a5205e182ae3    Coffee Shop
26   4b0c3889f964a520243923e3    Coffee Shop
27   5a981dbe0c9f3129c9ee442c    Coffee Shop
28   4db81aaa43a1a75c1f6afa6b    Coffee Shop
29   5b8431619f8a9f002c9bdc53    Coffee Shop
30   537d4d6d498ec171ba22e7fe    Coffee Shop
31   5a81ae339deb7d369fa7f146    Coffee Shop
32   576d30ed498ef2e95e26e6d0    Coffee Shop
33   568bcf61498e3aaff5e351f8    Coffee Shop
34   5a6b737b35f98359eed11974    Coffee Shop
35   576d6f42cd10a37101171051    Coffee Shop
36   565caeca498e1e36a503b42c    Coffee Shop
37   4bec073a6295c9b6815c8808    Coffee Shop
38   4b9e8c12f964a520d8ed36e3    Coffee Shop
39   4b9e7bbdf964a520e9e736e3    Coffee Shop
40   4dc9d2add4c07b350108956a    Coffee Shop
41   54132b3b498ee9ca9332e189    Coffee Shop
42   59cd51c71b0ea516e9e7b3aa    Coffee Shop
43   59f784dd28122f14f9d5d63d    Coffee Shop
44   4b0c001cf964a520853523e3    Coffee Shop
45   4b02c013f964a520aa4922e3    Coffee Shop
46   4e9abef19a52edbd6570cf18    Coffee Shop
47   5bdb42f93af988002c24bc8d    Coffee Shop
48   52e954c9498e28c9bf4cf7eb    Coffee Shop
49   506dd71be4b0a6dae803259a    Coffee Shop
50   4b9e710df964a5201ee436e3    Coffee Shop
51   53bd25f3498edd0cf854e13c    Coffee Shop
52   4b6b4340f964a520c9fc2be3    Coffee Shop
53   57f2c4f6498e6e70a25bfeb8    Coffee Shop
54   4b9e73dbf964a52023e536e3    Coffee Shop
55   5bdff325da5ede002c67d98a    Coffee Shop
56   53db870e498e43c1f94399b9    Coffee Shop
57   557f05ca498ec78ac7b29315    Coffee Shop
58   563d2f2dcd10bcf27ae37c3b    Coffee Shop
59   4ba3d8def964a520086638e3    Coffee Shop
60   554cab45498e01d1a2080230    Coffee Shop
61   4db81aaa43a1a75c1f6afa6b    Coffee Shop
62   53af56a1498ee47d2a3a06d7    Coffee Shop
63   51cf6105498e99bf4fc45d1b    Coffee Shop
64   56cf4d80498ebf41870d5317    Coffee Shop
65   55a40a8e498e0819937a8534    Coffee Shop
66   5249d69a11d2dc1056b45536    Coffee Shop
67   57b46745498e55186baa34c9    Coffee Shop
68   4cc6e4f4b3de9c74a8afb4c9    Coffee Shop
69   5592c393498ed517c4f6fc68    Coffee Shop
70   4ada6dfcf964a520842221e3    Coffee Shop
71   5be2a9041953f3002ce84f80    Coffee Shop
72   4b83ddb4f964a5204f1431e3    Coffee Shop
73   4cd2cd451cd32c0feb9470cf    Coffee Shop
74   4af302d7f964a520c4e921e3    Coffee Shop
75   564f3456498e9d0bc7152f88    Coffee Shop
76   4b8d7b70f964a52063fe32e3    Coffee Shop
77   4af5de4ff964a5200cfe21e3    Coffee Shop
78   4adcba1cf964a520272f21e3    Coffee Shop
79   59cd51c71b0ea516e9e7b3aa    Coffee Shop
80   563d2f2dcd10bcf27ae37c3b    Coffee Shop
81   4b0c001cf964a520853523e3    Coffee Shop
82   557f05ca498ec78ac7b29315    Coffee Shop
83   54132b3b498ee9ca9332e189    Coffee Shop
84   4b8bce0af964a52038ac32e3    Coffee Shop
85   52e954c9498e28c9bf4cf7eb    Coffee Shop
86   4ccb0e7faa25a35d37920b0f    Coffee Shop
87   4b9e73dbf964a52023e536e3    Coffee Shop
88   4b981b46f96

We will have to slice dataframe into 3 dataframes run the code to get ratings for each coffe shop and then merge it back together due to Foursquare limitations.

Lets name our data slices nearby_venues_part1, nearby_venues_part2 and nearby_venues_part3


In [167]:
venues_list2=[]
for venueid in Toronto_rating2['Venue ID'][0:156]:
    print(venueid)
    url1 = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
            venueid,
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION 
            )
            
    result = requests.get(url1).json()['response']       
    
    for v in result:
        try:
            venues_list2.append([
                venueid,
                result['venue']['rating']])
            
        except:
            venues_list2.append([
                venueid,
                'NaN'])
                    
tnearby_venues2 = pd.DataFrame(venues_list2, columns=['Venue ID','Ratings'])

53b8466a498e83df908c3f21
57cd9d20498e6ab8342980e2
5619551a498e9e35fce2256b
51853a73498e4d97a8b20831
58c7fbf7424f9373e6427e99
581258b738fa5bbefe4c0857
4b2cf78cf964a52077cb24e3
5a81ae339deb7d369fa7f146
4b9e7418f964a52032e536e3
4bc3360374a9a593692ed4f6
4d077daee350b60c3bbb9242
4e9de9fbb803b7506dcf4c41
4fb13c20e4b011e6f93513c0
57d32c53498e983542aa781c
4af1939bf964a5206de121e3
4e776dd788775d593ed36897
4b7aa994f964a5200c362fe3
5a39970cc6666622a0eae5d0
565caeca498e1e36a503b42c
4b5219ccf964a520d56727e3
4fff1f96e4b042ae8acddca5
57963897498e6873394a559d
5b8431619f8a9f002c9bdc53
4dadd38a0cb6f003f490e329
54f9c6de498eb5e6895c94b2
4b619337f964a5205e182ae3
4b0c3889f964a520243923e3
5a981dbe0c9f3129c9ee442c
4db81aaa43a1a75c1f6afa6b
5b8431619f8a9f002c9bdc53
537d4d6d498ec171ba22e7fe
5a81ae339deb7d369fa7f146
576d30ed498ef2e95e26e6d0
568bcf61498e3aaff5e351f8
5a6b737b35f98359eed11974
576d6f42cd10a37101171051
565caeca498e1e36a503b42c
4bec073a6295c9b6815c8808
4b9e8c12f964a520d8ed36e3
4b9e7bbdf964a520e9e736e3


Let's see if datfarem is filled

In [168]:
tnearby_venues2.shape

(156, 2)

In [169]:
tnearby_venues_ratings = tnearby_venues2
tnearby_venues_ratings

Venue ID Ratings
0    53b8466a498e83df908c3f21     8.9
1    57cd9d20498e6ab8342980e2     8.8
2    5619551a498e9e35fce2256b     8.3
3    51853a73498e4d97a8b20831     8.6
4    58c7fbf7424f9373e6427e99     7.8
5    581258b738fa5bbefe4c0857     6.7
6    4b2cf78cf964a52077cb24e3     6.6
7    5a81ae339deb7d369fa7f146     9.1
8    4b9e7418f964a52032e536e3     7.3
9    4bc3360374a9a593692ed4f6     6.8
10   4d077daee350b60c3bbb9242     6.9
11   4e9de9fbb803b7506dcf4c41       7
12   4fb13c20e4b011e6f93513c0     6.7
13   57d32c53498e983542aa781c     6.9
14   4af1939bf964a5206de121e3     6.6
15   4e776dd788775d593ed36897     6.6
16   4b7aa994f964a5200c362fe3     6.6
17   5a39970cc6666622a0eae5d0     6.9
18   565caeca498e1e36a503b42c     6.8
19   4b5219ccf964a520d56727e3     6.7
20   4fff1f96e4b042ae8acddca5     8.6
21   57963897498e6873394a559d     8.1
22   5b8431619f8a9f002c9bdc53     6.9
23   4dadd38a0cb6f003f490e329     6.8
24   54f9c6de498eb5e6895c94b2     6.6
25   4b619337f964a5205e182ae3     6.6
26   4b0c3889f964a520243923e3     6.2
27   5a981dbe0c9f3129c9ee442c     7.7
28   4db81aaa43a1a75c1f6afa6b     7.3
29   5b8431619f8a9f002c9bdc53     6.9
30   537d4d6d498ec171ba22e7fe     8.1
31   5a81ae339deb7d369fa7f146     9.1
32   576d30ed498ef2e95e26e6d0     7.7
33   568bcf61498e3aaff5e351f8     7.7
34   5a6b737b35f98359eed11974     8.2
35   576d6f42cd10a37101171051     6.8
36   565caeca498e1e36a503b42c     6.8
37   4bec073a6295c9b6815c8808     6.3
38   4b9e8c12f964a520d8ed36e3     6.5
39   4b9e7bbdf964a520e9e736e3     6.1
40   4dc9d2add4c07b350108956a       7
41   54132b3b498ee9ca9332e189     8.2
42   59cd51c71b0ea516e9e7b3aa     8.2
43   59f784dd28122f14f9d5d63d     7.8
44   4b0c001cf964a520853523e3     7.8
45   4b02c013f964a520aa4922e3     6.9
46   4e9abef19a52edbd6570cf18     6.8
47   5bdb42f93af988002c24bc8d     6.8
48   52e954c9498e28c9bf4cf7eb     7.3
49   506dd71be4b0a6dae803259a     7.3
50   4b9e710df964a5201ee436e3       7
51   53bd25f3498edd0cf854e13c       7
52   4b6b4340f964a520c9fc2be3     7.1
53   57f2c4f6498e6e70a25bfeb8     7.1
54   4b9e73dbf964a52023e536e3     6.8
55   5bdff325da5ede002c67d98a     6.8
56   53db870e498e43c1f94399b9     6.7
57   557f05ca498ec78ac7b29315     7.8
58   563d2f2dcd10bcf27ae37c3b     8.1
59   4ba3d8def964a520086638e3     6.9
60   554cab45498e01d1a2080230     6.8
61   4db81aaa43a1a75c1f6afa6b     7.3
62   53af56a1498ee47d2a3a06d7     6.9
63   51cf6105498e99bf4fc45d1b     6.5
64   56cf4d80498ebf41870d5317     6.7
65   55a40a8e498e0819937a8534     6.5
66   5249d69a11d2dc1056b45536     6.6
67   57b46745498e55186baa34c9     6.4
68   4cc6e4f4b3de9c74a8afb4c9     6.3
69   5592c393498ed517c4f6fc68     6.4
70   4ada6dfcf964a520842221e3     6.2
71   5be2a9041953f3002ce84f80     6.2
72   4b83ddb4f964a5204f1431e3     6.2
73   4cd2cd451cd32c0feb9470cf     6.3
74   4af302d7f964a520c4e921e3     7.8
75   564f3456498e9d0bc7152f88     8.2
76   4b8d7b70f964a52063fe32e3       7
77   4af5de4ff964a5200cfe21e3     6.5
78   4adcba1cf964a520272f21e3     5.9
79   59cd51c71b0ea516e9e7b3aa     8.2
80   563d2f2dcd10bcf27ae37c3b     8.1
81   4b0c001cf964a520853523e3     7.8
82   557f05ca498ec78ac7b29315     7.8
83   54132b3b498ee9ca9332e189     8.2
84   4b8bce0af964a52038ac32e3     7.1
85   52e954c9498e28c9bf4cf7eb     7.3
86   4ccb0e7faa25a35d37920b0f     6.9
87   4b9e73dbf964a52023e536e3     6.8
88   4b981b46f964a520c22c35e3     6.6
89   4dadd38a0cb6f003f490e329     6.8
90   5b8431619f8a9f002c9bdc53     6.9
91   4b619337f964a5205e182ae3     6.6
92   544e9ee6498e2c55cc71bd07     7.9
93   5374b6f4498e371df1066313     8.1
94   5b86857a1fa763002c84f269     NaN
95   59cd51c71b0ea516e9e7b3aa     8.2
96   4b0c001cf964a520853523e3     7.8
97   563d2f2dcd10bcf27ae37c3b     8.1
98   506dd71be4b0a6dae803259a     7.3
99   52e954c9498e28c9bf4cf7eb     7.3
100  54132b3b498ee9ca9332e189     8.2
101  4b8bce0af964a52038ac32e3     7.1
102  57963897498e6873394a559d     8.1
103  53bd25f3498edd0cf854e13c       7
104  557f05ca498ec78ac7b29315  

Let's remove dublicate values

In [172]:
tnearby_venues_ratings = tnearby_venues_ratings.drop_duplicates(subset=['Venue ID']).reset_index(drop=True)
tnearby_venues_ratings

Venue ID Ratings
0    53b8466a498e83df908c3f21     8.9
1    57cd9d20498e6ab8342980e2     8.8
2    5619551a498e9e35fce2256b     8.3
3    51853a73498e4d97a8b20831     8.6
4    58c7fbf7424f9373e6427e99     7.8
5    581258b738fa5bbefe4c0857     6.7
6    4b2cf78cf964a52077cb24e3     6.6
7    5a81ae339deb7d369fa7f146     9.1
8    4b9e7418f964a52032e536e3     7.3
9    4bc3360374a9a593692ed4f6     6.8
10   4d077daee350b60c3bbb9242     6.9
11   4e9de9fbb803b7506dcf4c41       7
12   4fb13c20e4b011e6f93513c0     6.7
13   57d32c53498e983542aa781c     6.9
14   4af1939bf964a5206de121e3     6.6
15   4e776dd788775d593ed36897     6.6
16   4b7aa994f964a5200c362fe3     6.6
17   5a39970cc6666622a0eae5d0     6.9
18   565caeca498e1e36a503b42c     6.8
19   4b5219ccf964a520d56727e3     6.7
20   4fff1f96e4b042ae8acddca5     8.6
21   57963897498e6873394a559d     8.1
22   5b8431619f8a9f002c9bdc53     6.9
23   4dadd38a0cb6f003f490e329     6.8
24   54f9c6de498eb5e6895c94b2     6.6
25   4b619337f964a5205e182ae3     6.6
26   4b0c3889f964a520243923e3     6.2
27   5a981dbe0c9f3129c9ee442c     7.7
28   4db81aaa43a1a75c1f6afa6b     7.3
29   537d4d6d498ec171ba22e7fe     8.1
30   576d30ed498ef2e95e26e6d0     7.7
31   568bcf61498e3aaff5e351f8     7.7
32   5a6b737b35f98359eed11974     8.2
33   576d6f42cd10a37101171051     6.8
34   4bec073a6295c9b6815c8808     6.3
35   4b9e8c12f964a520d8ed36e3     6.5
36   4b9e7bbdf964a520e9e736e3     6.1
37   4dc9d2add4c07b350108956a       7
38   54132b3b498ee9ca9332e189     8.2
39   59cd51c71b0ea516e9e7b3aa     8.2
40   59f784dd28122f14f9d5d63d     7.8
41   4b0c001cf964a520853523e3     7.8
42   4b02c013f964a520aa4922e3     6.9
43   4e9abef19a52edbd6570cf18     6.8
44   5bdb42f93af988002c24bc8d     6.8
45   52e954c9498e28c9bf4cf7eb     7.3
46   506dd71be4b0a6dae803259a     7.3
47   4b9e710df964a5201ee436e3       7
48   53bd25f3498edd0cf854e13c       7
49   4b6b4340f964a520c9fc2be3     7.1
50   57f2c4f6498e6e70a25bfeb8     7.1
51   4b9e73dbf964a52023e536e3     6.8
52   5bdff325da5ede002c67d98a     6.8
53   53db870e498e43c1f94399b9     6.7
54   557f05ca498ec78ac7b29315     7.8
55   563d2f2dcd10bcf27ae37c3b     8.1
56   4ba3d8def964a520086638e3     6.9
57   554cab45498e01d1a2080230     6.8
58   53af56a1498ee47d2a3a06d7     6.9
59   51cf6105498e99bf4fc45d1b     6.5
60   56cf4d80498ebf41870d5317     6.7
61   55a40a8e498e0819937a8534     6.5
62   5249d69a11d2dc1056b45536     6.6
63   57b46745498e55186baa34c9     6.4
64   4cc6e4f4b3de9c74a8afb4c9     6.3
65   5592c393498ed517c4f6fc68     6.4
66   4ada6dfcf964a520842221e3     6.2
67   5be2a9041953f3002ce84f80     6.2
68   4b83ddb4f964a5204f1431e3     6.2
69   4cd2cd451cd32c0feb9470cf     6.3
70   4af302d7f964a520c4e921e3     7.8
71   564f3456498e9d0bc7152f88     8.2
72   4b8d7b70f964a52063fe32e3       7
73   4af5de4ff964a5200cfe21e3     6.5
74   4adcba1cf964a520272f21e3     5.9
75   4b8bce0af964a52038ac32e3     7.1
76   4ccb0e7faa25a35d37920b0f     6.9
77   4b981b46f964a520c22c35e3     6.6
78   544e9ee6498e2c55cc71bd07     7.9
79   5374b6f4498e371df1066313     8.1
80   5b86857a1fa763002c84f269     NaN
81   4ad78ecaf964a520220c21e3     8.4
82   4ae0c900f964a520718221e3     7.5
83   4ade03e3f964a5205d6721e3     6.4
84   5508810b498e56b2576b2070     6.6
85   4aec6bbaf964a520e6c621e3     6.5
86   55d2781b498e82585d37691e     7.7
87   4b0fd74af964a5205d6523e3     6.6
88   5550e0c9498ea5830a839f06     6.7
89   4b0ade4cf964a5202e2923e3     6.1
90   4f79e8a1e4b03b459fae7e97     6.9
91   4b62d9d0f964a5207a552ae3     6.3
92   4b9e7451f964a52044e536e3     6.6
93   4b9e7c03f964a52001e836e3     6.5
94   4ceea9468212548121e465a1     5.8
95   4dceaf5db0fb25f6e349cae3     8.3
96   4b264649f964a520be7924e3     6.4
97   4d32fb2deefa8cfada643cb3     5.7
98   57dd9347cd10fabfa7c7fa62     NaN
99   5830bf495d6ec631f622902f     8.5
100  4adb5a00f964a5204c2621e3     7.7
101  4bc39d9b4cdfc9b6b09e9721     6.7
102  590a0b5cda2e007acf8eb4a4     6.7
103  53fd3897498ea15f71e72ea9     6.1
104  5553954a498e8e11bc49ecf2  

Let's remove Nan Ratings

In [177]:
tnearby_venues_ratings = tnearby_venues_ratings[~tnearby_venues_ratings['Ratings'].isin(['NaN'])].reset_index(drop=True)
tnearby_venues_ratings

Venue ID Ratings
0    53b8466a498e83df908c3f21     8.9
1    57cd9d20498e6ab8342980e2     8.8
2    5619551a498e9e35fce2256b     8.3
3    51853a73498e4d97a8b20831     8.6
4    58c7fbf7424f9373e6427e99     7.8
5    581258b738fa5bbefe4c0857     6.7
6    4b2cf78cf964a52077cb24e3     6.6
7    5a81ae339deb7d369fa7f146     9.1
8    4b9e7418f964a52032e536e3     7.3
9    4bc3360374a9a593692ed4f6     6.8
10   4d077daee350b60c3bbb9242     6.9
11   4e9de9fbb803b7506dcf4c41       7
12   4fb13c20e4b011e6f93513c0     6.7
13   57d32c53498e983542aa781c     6.9
14   4af1939bf964a5206de121e3     6.6
15   4e776dd788775d593ed36897     6.6
16   4b7aa994f964a5200c362fe3     6.6
17   5a39970cc6666622a0eae5d0     6.9
18   565caeca498e1e36a503b42c     6.8
19   4b5219ccf964a520d56727e3     6.7
20   4fff1f96e4b042ae8acddca5     8.6
21   57963897498e6873394a559d     8.1
22   5b8431619f8a9f002c9bdc53     6.9
23   4dadd38a0cb6f003f490e329     6.8
24   54f9c6de498eb5e6895c94b2     6.6
25   4b619337f964a5205e182ae3     6.6
26   4b0c3889f964a520243923e3     6.2
27   5a981dbe0c9f3129c9ee442c     7.7
28   4db81aaa43a1a75c1f6afa6b     7.3
29   537d4d6d498ec171ba22e7fe     8.1
30   576d30ed498ef2e95e26e6d0     7.7
31   568bcf61498e3aaff5e351f8     7.7
32   5a6b737b35f98359eed11974     8.2
33   576d6f42cd10a37101171051     6.8
34   4bec073a6295c9b6815c8808     6.3
35   4b9e8c12f964a520d8ed36e3     6.5
36   4b9e7bbdf964a520e9e736e3     6.1
37   4dc9d2add4c07b350108956a       7
38   54132b3b498ee9ca9332e189     8.2
39   59cd51c71b0ea516e9e7b3aa     8.2
40   59f784dd28122f14f9d5d63d     7.8
41   4b0c001cf964a520853523e3     7.8
42   4b02c013f964a520aa4922e3     6.9
43   4e9abef19a52edbd6570cf18     6.8
44   5bdb42f93af988002c24bc8d     6.8
45   52e954c9498e28c9bf4cf7eb     7.3
46   506dd71be4b0a6dae803259a     7.3
47   4b9e710df964a5201ee436e3       7
48   53bd25f3498edd0cf854e13c       7
49   4b6b4340f964a520c9fc2be3     7.1
50   57f2c4f6498e6e70a25bfeb8     7.1
51   4b9e73dbf964a52023e536e3     6.8
52   5bdff325da5ede002c67d98a     6.8
53   53db870e498e43c1f94399b9     6.7
54   557f05ca498ec78ac7b29315     7.8
55   563d2f2dcd10bcf27ae37c3b     8.1
56   4ba3d8def964a520086638e3     6.9
57   554cab45498e01d1a2080230     6.8
58   53af56a1498ee47d2a3a06d7     6.9
59   51cf6105498e99bf4fc45d1b     6.5
60   56cf4d80498ebf41870d5317     6.7
61   55a40a8e498e0819937a8534     6.5
62   5249d69a11d2dc1056b45536     6.6
63   57b46745498e55186baa34c9     6.4
64   4cc6e4f4b3de9c74a8afb4c9     6.3
65   5592c393498ed517c4f6fc68     6.4
66   4ada6dfcf964a520842221e3     6.2
67   5be2a9041953f3002ce84f80     6.2
68   4b83ddb4f964a5204f1431e3     6.2
69   4cd2cd451cd32c0feb9470cf     6.3
70   4af302d7f964a520c4e921e3     7.8
71   564f3456498e9d0bc7152f88     8.2
72   4b8d7b70f964a52063fe32e3       7
73   4af5de4ff964a5200cfe21e3     6.5
74   4adcba1cf964a520272f21e3     5.9
75   4b8bce0af964a52038ac32e3     7.1
76   4ccb0e7faa25a35d37920b0f     6.9
77   4b981b46f964a520c22c35e3     6.6
78   544e9ee6498e2c55cc71bd07     7.9
79   5374b6f4498e371df1066313     8.1
80   4ad78ecaf964a520220c21e3     8.4
81   4ae0c900f964a520718221e3     7.5
82   4ade03e3f964a5205d6721e3     6.4
83   5508810b498e56b2576b2070     6.6
84   4aec6bbaf964a520e6c621e3     6.5
85   55d2781b498e82585d37691e     7.7
86   4b0fd74af964a5205d6523e3     6.6
87   5550e0c9498ea5830a839f06     6.7
88   4b0ade4cf964a5202e2923e3     6.1
89   4f79e8a1e4b03b459fae7e97     6.9
90   4b62d9d0f964a5207a552ae3     6.3
91   4b9e7451f964a52044e536e3     6.6
92   4b9e7c03f964a52001e836e3     6.5
93   4ceea9468212548121e465a1     5.8
94   4dceaf5db0fb25f6e349cae3     8.3
95   4b264649f964a520be7924e3     6.4
96   4d32fb2deefa8cfada643cb3     5.7
97   5830bf495d6ec631f622902f     8.5
98   4adb5a00f964a5204c2621e3     7.7
99   4bc39d9b4cdfc9b6b09e9721     6.7
100  590a0b5cda2e007acf8eb4a4     6.7
101  53fd3897498ea15f71e72ea9     6.1
102  5553954a498e8e11bc49ecf2     6.9
103  4ad79243f964a5204c0c21e3     6.9
104  4c2745a8c11dc9b6af4a2a24  

Let's check how many venues were returned for each neighborhood

In [115]:
Toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            46   
Brockton, Parkdale Village, Exhibition Place                           22   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Central Bay Street                                                     64   
Christie                                                               15   
Church and Wellesley                                                   66   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             26   
Davisville North                                                        8   
Dufferin, Dovercourt Village                                           16   
Enclave of M4L                                                         15   
Enclave of M5E                                                         84   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          18   
India Bazaar, The Beaches West                                         15   
Kensington Market, Chinatown, Grange Park                              56   
Lawrence Park                                                           4   
Little Portugal, Trinity                                               42   
Moore Park, Summerhill East                                             2   
North Toronto West                                                     17   
Parkdale, Roncesvalles                                                 12   
Regent Park, Harbourfront                                              43   
Richmond, Adelaide, King                                              100   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     37   
St. James Town                                                         82   
St. James Town, Cabbagetown                                            35   
Studio District                                                        26   
Summerhill West, Rathnelly, South Hill, Forest ...                      9   
The Annex, North Midtown, Yorkville                                    18   
The Beaches                                                             4   
The Danforth  East                                                      4   
The Danforth West, Riverdale                                           42   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         36   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             46   
Brockton, Parkdale Village, Exhibition Place                            22   
CN Tower, King and Spadina, Railway Lands, Harb...                      16   
Central Bay Street                                                      64   
Christie                                                                15   
Church and Wellesley                                                    66   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              26   
Davisville North                                                         8   
Dufferin, Dovercourt Village        

Let's find out how many unique categories can be curated from all the returned venues

In [148]:
print('There are {} uniques categories.'.format(len(Toronto_venues['Venue Category'].unique())))

There are 218 uniques categories.


Analyze Each Neighborhood by category

In [149]:
# one hot encoding
Toronto_onehot = pd.get_dummies(Toronto_venues['Venue Category'], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Toronto_onehot['Neighborhood Real'] = Toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Toronto_onehot.columns[-1]] + list(Toronto_onehot.columns[:-1])
Toronto_onehot = Toronto_onehot[fixed_columns]

#check result
Toronto_onehot.head()

Neighborhood Real  Adult Boutique  Afghan Restaurant  Airport  \
0  Regent Park, Harbourfront               0                  0        0   
1  Regent Park, Harbourfront               0                  0        0   
2  Regent Park, Harbourfront               0                  0        0   
3  Regent Park, Harbourfront               0                  0        0   
4  Regent Park, Harbourfront               0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Workshop  \
0                    0                 0                   0              0   
1                    0                 0                   0              0   
2                    0                 0                   0              0   
3                    0                 0                   0              0   
4                    0                 0                   0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  \
0          0           0           0       0     0    0                 0   
1          0           0           0       1     0    0                 0   
2          0           0           0       0     0    0                 0   
3          0           0           0       0     0    0                 0   
4          0           0           0       0     0    0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                   0       0              0          0         0   
1                   0       0              0          0         0   
2                   0       0              0          0         0   
3                   0       0              0          0         0   
4                   0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  \
0                     0               0        0                0   
1                     0               0        0                0   
2                     0               0        0                0   
3                     0               0        0                0   
4                     0               0        0                0   

   Burger Joint  Burrito Place  Bus Line  Business Service  Butcher  Café  \
0             0              0         0                 0        0     0   
1             0              0         0                 0        0     0   
2             0              0         0                 0        0     0   
3             0              0         0                 0        0     0   
4             0              0         0              

And let's examine the new dataframe size.

In [150]:
Toronto_onehot.shape

(1490, 219)

Grouping rows by neighborhood and by taking the mean of the frequency of occurrence of each category.

In [151]:
Toronto_grouped = Toronto_onehot.groupby('Neighborhood Real').mean().reset_index()
Toronto_grouped

Neighborhood Real  Adult Boutique  \
0                                         Berczy Park        0.000000   
1        Brockton, Parkdale Village, Exhibition Place        0.000000   
2   CN Tower, King and Spadina, Railway Lands, Har...        0.000000   
3                                  Central Bay Street        0.000000   
4                                            Christie        0.000000   
5                                Church and Wellesley        0.015152   
6                      Commerce Court, Victoria Hotel        0.000000   
7                                          Davisville        0.000000   
8                                    Davisville North        0.000000   
9                        Dufferin, Dovercourt Village        0.000000   
10                                     Enclave of M4L        0.000000   
11                                     Enclave of M5E        0.000000   
12             First Canadian Place, Underground city        0.000000   
13                           Forest Hill North & West        0.000000   
14                           Garden District, Ryerson        0.000000   
15  Harbourfront East, Union Station, Toronto Islands        0.000000   
16                      High Park, The Junction South        0.000000   
17                     India Bazaar, The Beaches West        0.000000   
18          Kensington Market, Chinatown, Grange Park        0.000000   
19                                      Lawrence Park        0.000000   
20                           Little Portugal, Trinity        0.000000   
21                        Moore Park, Summerhill East        0.000000   
22                                 North Toronto West        0.000000   
23                             Parkdale, Roncesvalles        0.000000   
24                          Regent Park, Harbourfront        0.000000   
25                           Richmond, Adelaide, King        0.000000   
26                                           Rosedale        0.000000   
27                                           Roselawn        0.000000   
28                                 Runnymede, Swansea        0.000000   
29                                     St. James Town        0.000000   
30                        St. James Town, Cabbagetown        0.000000   
31                                    Studio District        0.000000   
32  Summerhill West, Rathnelly, South Hill, Forest...        0.000000   
33                The Annex, North Midtown, Yorkville        0.000000   
34                                        The Beaches        0.000000   
35                                 The Danforth  East        0.000000   
36                       The Danforth West, Riverdale        0.000000   
37           Toronto Dominion Centre, Design Exchange        0.000000   
38                     University of Toronto, Harbord        0.000000   

    Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0.000000   0.0000              0.0000        0.0000   
1            0.000000   0.0000              0.0000        0.0000   
2            0.000000   0.0625              0.0625        0.0625   
3            0.000000   0.0000              0.0000        0.0000   
4            0.000000   0.0000              0.0000        0.0000   
5            0.015152   0.0000              0.0000        0.0000   
6            0.000000   0.0000              0.0000        0.0000   
7            0.000000   0.0000              0.0000        0.0000   
8            0.000000   0.0000              0.0000        0.0000   
9            0.000000   0.0000              0.0000        0.0000   
10           0.000000   0.0000              0.0000        0.0000   
11           0.000000   0.0000              0.0000        0.0000   
12           0.000000   0.0000              0.0000        0.0000   
13           0.000000   0.0000              0.0000        0.0000   
14           0.000000   0.0000              0.0000        0.0000   
15           0.000000   0.0

Confirming the new size

In [152]:
Toronto_grouped.shape

(39, 219)

Let's write a function to sort the venues in descending order.

In [153]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Let's create the new dataframe and display the top 10 venues for each neighborhood.

In [154]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Toronto_grouped['Neighborhood Real']

for ind in np.arange(Toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park        Sandwich Place   
1       Brockton, Parkdale Village, Exhibition Place        Breakfast Spot   
2  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
3                                 Central Bay Street           Coffee Shop   
4                                           Christie         Grocery Store   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0           Coffee Shop          Cocktail Bar                Bakery   
1        Sandwich Place           Coffee Shop                  Café   
2      Airport Terminal        Airport Lounge       Harbor / Marina   
3        Sandwich Place      Sushi Restaurant                  Café   
4                  Café                  Park           Coffee Shop   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0      Seafood Restaurant              Beer Bar        Farmers Market   
1  Furniture / Home Store            Restaurant               Stadium   
2     Rental Car Location      Sculpture Garden              Boutique   
3      Italian Restaurant   Japanese Restaurant            Restaurant   
4               Nightclub            Baby Store    Italian Restaurant   

           8th Most Common Venue 9th Most Common Venue  \
0  Vegetarian / Vegan Restaurant           Cheese Shop   
1                            Bar                Bakery   
2                  Boat or Ferry                 Plane   
3                           Bank           Pizza Place   
4                     Restaurant    Athletics & Sports   

      10th Most Common Venue  
0    Comfort Food Restaurant  
1        Japanese Restaurant  
2                    Airport  
3  Middle Eastern Restaurant  
4             Cosmetics Shop

Cluster Neighborhoods

Run k-means to cluster the neighborhood into 5 clusters.

In [155]:
# set number of clusters
kclusters = 5

Toronto_grouped_clustering = Toronto_grouped.drop('Neighborhood Real', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [156]:
neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue  \
0                                         Berczy Park        Sandwich Place   
1        Brockton, Parkdale Village, Exhibition Place        Breakfast Spot   
2   CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
3                                  Central Bay Street           Coffee Shop   
4                                            Christie         Grocery Store   
5                                Church and Wellesley   Japanese Restaurant   
6                      Commerce Court, Victoria Hotel           Coffee Shop   
7                                          Davisville           Pizza Place   
8                                    Davisville North      Department Store   
9                        Dufferin, Dovercourt Village              Pharmacy   
10                                     Enclave of M4L    Light Rail Station   
11                                     Enclave of M5E        Sandwich Place   
12             First Canadian Place, Underground city           Coffee Shop   
13                           Forest Hill North & West                  Park   
14                           Garden District, Ryerson           Coffee Shop   
15  Harbourfront East, Union Station, Toronto Islands           Coffee Shop   
16                      High Park, The Junction South    Mexican Restaurant   
17                     India Bazaar, The Beaches West  Fast Food Restaurant   
18          Kensington Market, Chinatown, Grange Park                  Café   
19                                      Lawrence Park      Business Service   
20                           Little Portugal, Trinity                   Bar   
21                        Moore Park, Summerhill East          Tennis Court   
22                                 North Toronto West           Coffee Shop   
23                             Parkdale, Roncesvalles           Coffee Shop   
24                          Regent Park, Harbourfront           Coffee Shop   
25                           Richmond, Adelaide, King           Coffee Shop   
26                                           Rosedale                  Park   
27                                           Roselawn                Garden   
28                                 Runnymede, Swansea           Coffee Shop   
29                                     St. James Town           Coffee Shop   
30                        St. James Town, Cabbagetown           Coffee Shop   
31                                    Studio District           Coffee Shop   
32  Summerhill West, Rathnelly, South Hill, Forest...           Coffee Shop   
33                The Annex, North Midtown, Yorkville        Sandwich Place   
34                                        The Beaches          Neighborhood   
35                                 The Danforth  East                  Park   
36                       The Danforth West, Riverdale      Greek Restaurant   
37           Toronto Dominion Centre, Design Exchange           Coffee Shop   
38                     University of Toronto, Harbord                  Café   

   2nd Most Common Venue          3rd Most Common Venue  \
0            Coffee Shop                   Cocktail Bar   
1         Sandwich Place                    Coffee Shop   
2       Airport Terminal                 Airport Lounge   
3         Sandwich Place               Sushi Restaurant   
4                   Café                           Park   
5       Sushi Restaurant                    Coffee Shop   
6                   Café                 Sandwich Place   
7       Sushi Restaurant                            Gym   
8   Gym / Fitness Center                     Playground   
9            Supermarket                      Wine Shop   
10           Pizza Place                  Auto Workshop   
11           Coffee Shop                           Bank   
12        Sandwich Place                           Café   
13                 Trail                  Jewelry Stor

In [157]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Toronto_merged = Toronto_data2

# merge Toronto_grouped with Toronto_data to add latitude/longitude for each neighborhood
Toronto_merged = Toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

Toronto_merged.head() # check sirst columns!

PostalCode           Borough               Neighborhood   Latitude  \
0        M5A  Downtown Toronto  Regent Park, Harbourfront  43.654260   
1        M5B  Downtown Toronto   Garden District, Ryerson  43.657162   
2        M5C  Downtown Toronto             St. James Town  43.651494   
3        M4E      East Toronto                The Beaches  43.676357   
4        M5E  Downtown Toronto                Berczy Park  43.644771   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.360636               1           Coffee Shop                  Park   
1 -79.378937               1           Coffee Shop        Sandwich Place   
2 -79.375418               1           Coffee Shop                  Café   
3 -79.293031               3          Neighborhood           Music Venue   
4 -79.373306               1        Sandwich Place           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0                   Pub                  Café                       Bakery   
1        Clothing Store                  Café                         Bank   
2    Italian Restaurant          Cocktail Bar               Clothing Store   
3     Health Food Store                   Pub  Eastern European Restaurant   
4          Cocktail Bar                Bakery           Seafood Restaurant   

  6th Most Common Venue 7th Most Common Venue          8th Most Common Venue  \
0            Restaurant   Distribution Center                    Event Space   
1                 Hotel   Japanese Restaurant                 Cosmetics Shop   
2            Restaurant                 Diner            Japanese Restaurant   
3            Donut Shop      Doner Restaurant                        Dog Run   
4              Beer Bar        Farmers Market  Vegetarian / Vegan Restaurant   

  9th Most Common Venue   10th Most Common Venue  
0        Discount Store           Chocolate Shop  
1           Pizza Place                Bookstore  
2           Art Gallery           Farmers Market  
3   Distribution Center           Discount Store  
4           Cheese Shop  Comfort Food Restaurant

Let's drop 1st column.

In [181]:
Toronto_merged = Toronto_merged.drop(columns=['PostalCode'])
Toronto_merged.head()

Borough               Neighborhood   Latitude  Longitude  \
0  Downtown Toronto  Regent Park, Harbourfront  43.654260 -79.360636   
1  Downtown Toronto   Garden District, Ryerson  43.657162 -79.378937   
2  Downtown Toronto             St. James Town  43.651494 -79.375418   
3      East Toronto                The Beaches  43.676357 -79.293031   
4  Downtown Toronto                Berczy Park  43.644771 -79.373306   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               1           Coffee Shop                  Park   
1               1           Coffee Shop        Sandwich Place   
2               1           Coffee Shop                  Café   
3               3          Neighborhood           Music Venue   
4               1        Sandwich Place           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0                   Pub                  Café                       Bakery   
1        Clothing Store                  Café                         Bank   
2    Italian Restaurant          Cocktail Bar               Clothing Store   
3     Health Food Store                   Pub  Eastern European Restaurant   
4          Cocktail Bar                Bakery           Seafood Restaurant   

  6th Most Common Venue 7th Most Common Venue          8th Most Common Venue  \
0            Restaurant   Distribution Center                    Event Space   
1                 Hotel   Japanese Restaurant                 Cosmetics Shop   
2            Restaurant                 Diner            Japanese Restaurant   
3            Donut Shop      Doner Restaurant                        Dog Run   
4              Beer Bar        Farmers Market  Vegetarian / Vegan Restaurant   

  9th Most Common Venue   10th Most Common Venue  
0        Discount Store           Chocolate Shop  
1           Pizza Place                Bookstore  
2           Art Gallery           Farmers Market  
3   Distribution Center           Discount Store  
4           Cheese Shop  Comfort Food Restaurant

Let's visualize the resulting clusters

In [182]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Toronto_merged['Latitude'], Toronto_merged['Longitude'], Toronto_merged['Neighborhood'], Toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Examine Clusters

Cluster 1

In [183]:
Cluster1T = Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 0, Toronto_merged.columns[[1] + list(range(5, Toronto_merged.shape[1]))]]
Cluster1T

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
29  Moore Park, Summerhill East          Tennis Court            Restaurant   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
29          Dance Studio     Electronics Store  Eastern European Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
29            Donut Shop      Doner Restaurant               Dog Run   

   9th Most Common Venue 10th Most Common Venue  
29   Distribution Center         Discount Store

In [184]:
toronto_venues_coffee1 = Toronto_venues[(Toronto_venues['Neighborhood'].str.contains("Moore Park, Summerhill East")) & (Toronto_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
toronto_venues_coffee1

Empty DataFrame
Columns: [Neighborhood, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue ID, Venue Category]
Index: []

It looks like there is no Coffee Shops in this cluster

In [ ]:
Cluster1TJ = toronto_venues_coffee1.join(tnearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster1TJ 

Cluster 2

In [185]:
Cluster2T = Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 1, Toronto_merged.columns[[1] + list(range(5, Toronto_merged.shape[1]))]]
Cluster2T

Neighborhood 1st Most Common Venue  \
0                           Regent Park, Harbourfront           Coffee Shop   
1                            Garden District, Ryerson           Coffee Shop   
2                                      St. James Town           Coffee Shop   
4                                         Berczy Park        Sandwich Place   
5                                  Central Bay Street           Coffee Shop   
6                                            Christie         Grocery Store   
7                            Richmond, Adelaide, King           Coffee Shop   
8                        Dufferin, Dovercourt Village              Pharmacy   
10  Harbourfront East, Union Station, Toronto Islands           Coffee Shop   
11                           Little Portugal, Trinity                   Bar   
12                       The Danforth West, Riverdale      Greek Restaurant   
13           Toronto Dominion Centre, Design Exchange           Coffee Shop   
14       Brockton, Parkdale Village, Exhibition Place        Breakfast Spot   
15                     India Bazaar, The Beaches West  Fast Food Restaurant   
16                     Commerce Court, Victoria Hotel           Coffee Shop   
17                                    Studio District           Coffee Shop   
18                                      Lawrence Park      Business Service   
20                                   Davisville North      Department Store   
22                      High Park, The Junction South    Mexican Restaurant   
23                                 North Toronto West           Coffee Shop   
24                The Annex, North Midtown, Yorkville        Sandwich Place   
25                             Parkdale, Roncesvalles           Coffee Shop   
26                                         Davisville           Pizza Place   
27                     University of Toronto, Harbord                  Café   
28                                 Runnymede, Swansea           Coffee Shop   
30          Kensington Market, Chinatown, Grange Park                  Café   
31  Summerhill West, Rathnelly, South Hill, Forest...           Coffee Shop   
32  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
34                                     Enclave of M5E        Sandwich Place   
35                        St. James Town, Cabbagetown           Coffee Shop   
36             First Canadian Place, Underground city           Coffee Shop   
37                               Church and Wellesley   Japanese Restaurant   
38                                     Enclave of M4L    Light Rail Station   

   2nd Most Common Venue          3rd Most Common Venue  \
0                   Park                            Pub   
1         Sandwich Place                 Clothing Store   
2                   Café             Italian Restaurant   
4            Coffee Shop                   Cocktail Bar   
5         Sandwich Place               Sushi Restaurant   
6                   Café                           Park   
7                   Café                 Sandwich Place   
8            Supermarket                      Wine Shop   
10                 Hotel                           Café   
11                  Café        New American Restaurant   
12           Coffee Shop             Italian Restaurant   
13                  Café                 Sandwich Place   
14        Sandwich Place                    Coffee Shop   
15           Pizza Place              Food & Drink Shop   
16                  Café                 Sandwich Place   
17             Gastropub                           Café   
18              Bus Line                           Park   
20  Gym / Fitness Center                     Playground   
22                   Bar                           Café   
23        Clothing Store             Italian Restaurant   
24           Coffee Shop                           Café   
25                  Bank               Cuban Restaurant 

In [188]:
toronto_venues_coffee2 = Toronto_venues[(Toronto_venues['Neighborhood'].str.contains("Regent Park, Harbourfront|Garden District, Ryerson|St. James Town|Berczy Park|Central Bay Street|Christie|Richmond, Adelaide, King|Dufferin, Dovercourt Village|Harbourfront East, Union Station, Toronto Islands|Little Portugal, Trinity|The Danforth West, Riverdale|Toronto Dominion Centre, Design Exchange|Brockton, Parkdale Village, Exhibition Place|India Bazaar, The Beaches West|Commerce Court, Victoria Hotel|Studio District|Lawrence Park|Davisville North|High Park, The Junction South|North Toronto West|The Annex, North Midtown, Yorkville|Parkdale, Roncesvalles|Davisville|University of Toronto, Harbord|Runnymede, Swansea|Kensington Market, Chinatown, Grange Park|Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park|CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport|Enclave of M5E|St. James Town, Cabbagetown|First Canadian Place, Underground city|Church and Wellesley|Enclave of M4L")) & (Toronto_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
toronto_venues_coffee2

Neighborhood  Neighborhood Latitude  \
0                            Regent Park, Harbourfront              43.654260   
1                            Regent Park, Harbourfront              43.654260   
2                            Regent Park, Harbourfront              43.654260   
3                            Regent Park, Harbourfront              43.654260   
4                            Regent Park, Harbourfront              43.654260   
5                            Regent Park, Harbourfront              43.654260   
6                            Regent Park, Harbourfront              43.654260   
7                             Garden District, Ryerson              43.657162   
8                             Garden District, Ryerson              43.657162   
9                             Garden District, Ryerson              43.657162   
10                            Garden District, Ryerson              43.657162   
11                            Garden District, Ryerson              43.657162   
12                            Garden District, Ryerson              43.657162   
13                            Garden District, Ryerson              43.657162   
14                            Garden District, Ryerson              43.657162   
15                            Garden District, Ryerson              43.657162   
16                            Garden District, Ryerson              43.657162   
17                            Garden District, Ryerson              43.657162   
18                            Garden District, Ryerson              43.657162   
19                            Garden District, Ryerson              43.657162   
20                                      St. James Town              43.651494   
21                                      St. James Town              43.651494   
22                                      St. James Town              43.651494   
23                                      St. James Town              43.651494   
24                                      St. James Town              43.651494   
25                                      St. James Town              43.651494   
26                                      St. James Town              43.651494   
27                                         Berczy Park              43.644771   
28                                         Berczy Park              43.644771   
29                                         Berczy Park              43.644771   
30                                  Central Bay Street              43.657952   
31                                  Central Bay Street              43.657952   
32                                  Central Bay Street              43.657952   
33                                  Central Bay Street              43.657952   
34                                  Central Bay Street              43.657952   
35                                  Central Bay Street              43.657952   
36                                  Central Bay Street              43.657952   
37                                  Central Bay Street              43.657952   
38                                  Central Bay Street              43.657952   
39                                  Central Bay Street              43.657952   
40                                            Christie              43.669542   
41                            Richmond, Adelaide, King              43.650571   
42                            Richmond, Adelaide, King              43.650571   
43                            Richmond, Adelaide, King              43.650571   
44                            Richmond, Adelaide, King              43.650571   
45                            Richmond, Adelaide, King              43.650571   
46                            Richmond, Adelaide, King              43.650571   
47                            Richmond, Adelaide, King              43.650571   
48                            Richmond, Adelaide, King              43.65

In [190]:
Cluster2TJ = toronto_venues_coffee2.join(tnearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster2TJ 

Neighborhood  Neighborhood Latitude  \
0                            Regent Park, Harbourfront              43.654260   
1                            Regent Park, Harbourfront              43.654260   
2                            Regent Park, Harbourfront              43.654260   
3                            Regent Park, Harbourfront              43.654260   
4                            Regent Park, Harbourfront              43.654260   
5                            Regent Park, Harbourfront              43.654260   
6                            Regent Park, Harbourfront              43.654260   
7                             Garden District, Ryerson              43.657162   
8                             Garden District, Ryerson              43.657162   
9                             Garden District, Ryerson              43.657162   
10                            Garden District, Ryerson              43.657162   
11                            Garden District, Ryerson              43.657162   
12                            Garden District, Ryerson              43.657162   
13                            Garden District, Ryerson              43.657162   
14                            Garden District, Ryerson              43.657162   
15                            Garden District, Ryerson              43.657162   
16                            Garden District, Ryerson              43.657162   
17                            Garden District, Ryerson              43.657162   
18                            Garden District, Ryerson              43.657162   
19                            Garden District, Ryerson              43.657162   
20                                      St. James Town              43.651494   
21                                      St. James Town              43.651494   
22                                      St. James Town              43.651494   
23                                      St. James Town              43.651494   
24                                      St. James Town              43.651494   
25                                      St. James Town              43.651494   
26                                      St. James Town              43.651494   
27                                         Berczy Park              43.644771   
28                                         Berczy Park              43.644771   
29                                         Berczy Park              43.644771   
30                                  Central Bay Street              43.657952   
31                                  Central Bay Street              43.657952   
32                                  Central Bay Street              43.657952   
33                                  Central Bay Street              43.657952   
34                                  Central Bay Street              43.657952   
35                                  Central Bay Street              43.657952   
36                                  Central Bay Street              43.657952   
37                                  Central Bay Street              43.657952   
38                                  Central Bay Street              43.657952   
39                                  Central Bay Street              43.657952   
40                                            Christie              43.669542   
41                            Richmond, Adelaide, King              43.650571   
42                            Richmond, Adelaide, King              43.650571   
43                            Richmond, Adelaide, King              43.650571   
44                            Richmond, Adelaide, King              43.650571   
45                            Richmond, Adelaide, King              43.650571   
46                            Richmond, Adelaide, King              43.650571   
47                            Richmond, Adelaide, King              43.650571   
48                            Richmond, Adelaide, King              43.65

In [201]:
Cluster2TJ = Cluster2TJ[~Cluster2TJ['Ratings'].isin(['NaN'])].reset_index(drop=True)
Cluster2TJ

Neighborhood  Neighborhood Latitude  \
0                            Regent Park, Harbourfront              43.654260   
1                            Regent Park, Harbourfront              43.654260   
2                            Regent Park, Harbourfront              43.654260   
3                            Regent Park, Harbourfront              43.654260   
4                            Regent Park, Harbourfront              43.654260   
5                            Regent Park, Harbourfront              43.654260   
6                            Regent Park, Harbourfront              43.654260   
7                             Garden District, Ryerson              43.657162   
8                             Garden District, Ryerson              43.657162   
9                             Garden District, Ryerson              43.657162   
10                            Garden District, Ryerson              43.657162   
11                            Garden District, Ryerson              43.657162   
12                            Garden District, Ryerson              43.657162   
13                            Garden District, Ryerson              43.657162   
14                            Garden District, Ryerson              43.657162   
15                            Garden District, Ryerson              43.657162   
16                            Garden District, Ryerson              43.657162   
17                            Garden District, Ryerson              43.657162   
18                            Garden District, Ryerson              43.657162   
19                            Garden District, Ryerson              43.657162   
20                                      St. James Town              43.651494   
21                                      St. James Town              43.651494   
22                                      St. James Town              43.651494   
23                                      St. James Town              43.651494   
24                                      St. James Town              43.651494   
25                                      St. James Town              43.651494   
26                                      St. James Town              43.651494   
27                                         Berczy Park              43.644771   
28                                         Berczy Park              43.644771   
29                                         Berczy Park              43.644771   
30                                  Central Bay Street              43.657952   
31                                  Central Bay Street              43.657952   
32                                  Central Bay Street              43.657952   
33                                  Central Bay Street              43.657952   
34                                  Central Bay Street              43.657952   
35                                  Central Bay Street              43.657952   
36                                  Central Bay Street              43.657952   
37                                  Central Bay Street              43.657952   
38                                  Central Bay Street              43.657952   
39                                  Central Bay Street              43.657952   
40                                            Christie              43.669542   
41                            Richmond, Adelaide, King              43.650571   
42                            Richmond, Adelaide, King              43.650571   
43                            Richmond, Adelaide, King              43.650571   
44                            Richmond, Adelaide, King              43.650571   
45                            Richmond, Adelaide, King              43.650571   
46                            Richmond, Adelaide, King              43.650571   
47                            Richmond, Adelaide, King              43.650571   
48                            Richmond, Adelaide, King              43.65

Cluster 3

In [191]:
Cluster3T = Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 2, Toronto_merged.columns[[1] + list(range(5, Toronto_merged.shape[1]))]]
Cluster3T

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
9         The Danforth  East                  Park     Convenience Store   
21  Forest Hill North & West                  Park                 Trail   
33                  Rosedale                  Park            Playground   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9           Intersection           Yoga Studio      Department Store   
21         Jewelry Store      Sushi Restaurant           Yoga Studio   
33                 Trail           Yoga Studio          Dance Studio   

          6th Most Common Venue 7th Most Common Venue  \
9                   Escape Room     Electronics Store   
21             Department Store     Electronics Store   
33  Eastern European Restaurant            Donut Shop   

          8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
9   Eastern European Restaurant            Donut Shop       Doner Restaurant  
21  Eastern European Restaurant            Donut Shop       Doner Restaurant  
33             Doner Restaurant               Dog Run    Distribution Center

In [192]:
toronto_venues_coffee3 = Toronto_venues[(Toronto_venues['Neighborhood'].str.contains(" The Danforth East|Forest Hill North & West|Rosedale")) & (Toronto_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
toronto_venues_coffee3

Empty DataFrame
Columns: [Neighborhood, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue ID, Venue Category]
Index: []

It looks like there is no Coffee Shops in this cluster

In [ ]:
Cluster3TJ = toronto_venues_coffee3.join(tnearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster3TJ 

Cluster 4

In [193]:
Cluster4T = Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 3, Toronto_merged.columns[[1] + list(range(5, Toronto_merged.shape[1]))]]
Cluster4T

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3  The Beaches          Neighborhood           Music Venue   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
3     Health Food Store                   Pub  Eastern European Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3            Donut Shop      Doner Restaurant               Dog Run   

  9th Most Common Venue 10th Most Common Venue  
3   Distribution Center         Discount Store

In [194]:
toronto_venues_coffee4 = Toronto_venues[(Toronto_venues['Neighborhood'].str.contains("The Beaches")) & (Toronto_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
toronto_venues_coffee4

Neighborhood  Neighborhood Latitude  \
0  India Bazaar, The Beaches West              43.668999   

   Neighborhood Longitude          Venue  Venue Latitude  Venue Longitude  \
0              -79.315572  Country Style       43.667662       -79.312006   

                   Venue ID Venue Category  
0  5b86857a1fa763002c84f269    Coffee Shop

In [195]:
Cluster4TJ = toronto_venues_coffee4.join(tnearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster4TJ 

Neighborhood  Neighborhood Latitude  \
0  India Bazaar, The Beaches West              43.668999   

   Neighborhood Longitude          Venue  Venue Latitude  Venue Longitude  \
0              -79.315572  Country Style       43.667662       -79.312006   

                   Venue ID Venue Category Ratings  
0  5b86857a1fa763002c84f269    Coffee Shop     NaN

Cluster 5

In [196]:
Cluster5T = Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 4, Toronto_merged.columns[[1] + list(range(5, Toronto_merged.shape[1]))]]
Cluster5T

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
19     Roselawn                Garden           Music Venue   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
19           Yoga Studio         Deli / Bodega     Electronics Store   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
19  Eastern European Restaurant            Donut Shop      Doner Restaurant   

   9th Most Common Venue 10th Most Common Venue  
19               Dog Run    Distribution Center

In [197]:
toronto_venues_coffee5 = Toronto_venues[(Toronto_venues['Neighborhood'].str.contains("Roselawn")) & (Toronto_venues['Venue Category'].str.contains("Coffee Shop"))].reset_index(drop=True)
 
toronto_venues_coffee5

Empty DataFrame
Columns: [Neighborhood, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue ID, Venue Category]
Index: []

It looks like there is no Coffee Shops in this cluster

In [ ]:
Cluster5TJ = toronto_venues_coffee5.join(nearby_venues_ratings.set_index('Venue ID'), on = 'Venue ID')
Cluster5TJ 

Let's summerize Toronto results

In [203]:
data =[['Cluster1', 'No Coffee shops','No Coffee shops'], 
      ['Cluster2', Cluster2TJ["Ratings"].mean(),len(Cluster2TJ.index)],
      ['Cluster3', 'No Coffee shops','No Coffee shops'],
      ['Cluster4', 'No rating for Coffee shop',len(Cluster4TJ.index)],
      ['Cluster5', 'No Coffee shops','No Coffee shops']] 

dft = pd.DataFrame(data, columns = ['Toronto Cluster', 'Mean', 'Amount of Coffee Shops'])
dft

Toronto Cluster                       Mean Amount of Coffee Shops
0        Cluster1            No Coffee shops        No Coffee shops
1        Cluster2                     7.1719                    156
2        Cluster3            No Coffee shops        No Coffee shops
3        Cluster4  No rating for Coffee shop                      1
4        Cluster5            No Coffee shops        No Coffee shops

## Results

We have clustered the venues and the results for Manhatten are:

In [206]:
dfm

Manhattan Cluster      Mean  Amount of Coffee Shops
0          Cluster1  7.968627                      51
1          Cluster2  8.179592                      49
2          Cluster3  6.550000                       2
3          Cluster4  7.500000                       1
4          Cluster5  7.716667                       6

In [208]:
dfm.mean()

Mean                       7.582977
Amount of Coffee Shops    21.800000
dtype: float64

And for the Toronto central area:

In [207]:
dft

Toronto Cluster                       Mean Amount of Coffee Shops
0        Cluster1            No Coffee shops        No Coffee shops
1        Cluster2                     7.1719                    156
2        Cluster3            No Coffee shops        No Coffee shops
3        Cluster4  No rating for Coffee shop                      1
4        Cluster5            No Coffee shops        No Coffee shops

## Discussion section

From the Results we can definatly see that Toronto central area is much better area for a new Coffee shop than Manhatten. This is due to couple of factors.

Firstly, Toronto has only one cluster with a lot of Coffee shops so this tells us that there are more options to chose from if we want to open a new coffee shop.

Scecondly, we can see that the Toronto has a lower Coffee shop rating mean than Manhatten, which mean that there is a greater need of a good Coffee shop in the city and the competition is weaker.

## Conclusion

According to the data we have analyzed we can see that we should open new Coffee shop in one of the Toronto central areas with a cluster name of Cluster1, Cluster2 or Cluster5.

For further analysis we should include rental prices and the custumers flows.